Connected to .conda (Python 3.9.19)

In [1]:
import os
# import sys
# import IPython
import pandas as pd

In [2]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [3]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [4]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


<ipython-input-4-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


In [5]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [6]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

# dfTads = dfTads0.query('CompanyName == companyNamesVelo')
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'AmerenIP', 'Commonwealth Edison Co', 'Northern Municipal Power Agency', 'Northern Indiana Public Service Co LLC', 'Undetermined Company', 'American Transmission Co LLC'}
Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'American Transmission Company', 'Northern Indiana Public Service Company [BA', 'Commonwealth Edison Company', 'Ameren Services Company'}
{'100-199 kV', '200-299 kV', '600-799 kV', '300-399 kV'}
Size of TADS db after filtering: 16052, 47


In [7]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [8]:
import numpy as np

In [9]:
mA = np.random.rand(shape = (10, 10))
mB = np.random.rand(shape = (10, 10))

TypeError: rand() got an unexpected keyword argument 'shape'

In [10]:
mC = mA + mB

NameError: name 'mA' is not defined

In [11]:
mD = mA * mB

NameError: name 'mA' is not defined

In [12]:
mA = np.random.rand(shape = (10, 10))
mB = np.random.rand(shape = (10, 10))

TypeError: rand() got an unexpected keyword argument 'shape'

In [13]:
mA = np.random.rand((10, 10))
mB = np.random.rand(shape = (10, 10))

TypeError: 'tuple' object cannot be interpreted as an integer

In [14]:
mA = np.random.rand(10, 10)
mB = np.random.rand(10, 10)

In [15]:
mA

array([[0.50950866, 0.3875437 , 0.93582542, 0.57309684, 0.14989196,
        0.6409418 , 0.71530679, 0.69582249, 0.72637489, 0.31670226],
       [0.67028249, 0.84834603, 0.65299108, 0.97236924, 0.71533715,
        0.47264716, 0.43982044, 0.59066982, 0.02164214, 0.74203788],
       [0.16885034, 0.13045305, 0.88582675, 0.18846251, 0.59032846,
        0.65533344, 0.54446804, 0.5264089 , 0.3698716 , 0.45498995],
       [0.59792315, 0.5813624 , 0.72458451, 0.07774261, 0.89934662,
        0.89522689, 0.21911567, 0.17144204, 0.29029122, 0.59868038],
       [0.42311153, 0.01026964, 0.17632482, 0.02972556, 0.17336131,
        0.39694675, 0.30980321, 0.56023038, 0.78738844, 0.82838027],
       [0.95012464, 0.62530315, 0.14165816, 0.3959646 , 0.72908855,
        0.71262532, 0.79603933, 0.6595865 , 0.76997073, 0.11449327],
       [0.04657203, 0.5190496 , 0.57530042, 0.32247557, 0.7603077 ,
        0.51415526, 0.20045982, 0.96614656, 0.87489772, 0.46413032],
       [0.09074955, 0.48027545, 0.7501328

In [16]:
mB

array([[0.93456129, 0.31742004, 0.18833011, 0.47757742, 0.62902401,
        0.32909683, 0.78339204, 0.88109495, 0.30643319, 0.58982533],
       [0.36879601, 0.58960688, 0.17156786, 0.1696721 , 0.48723436,
        0.62994019, 0.18513088, 0.65935469, 0.42250558, 0.93309797],
       [0.51983609, 0.10319694, 0.98642627, 0.40971432, 0.22927701,
        0.64780426, 0.68993603, 0.07973429, 0.37913151, 0.52310432],
       [0.05644002, 0.08464586, 0.0228432 , 0.58744101, 0.38409318,
        0.90923149, 0.34598413, 0.33496317, 0.55119216, 0.59997725],
       [0.34953976, 0.99860469, 0.14712382, 0.18093245, 0.78051959,
        0.17099312, 0.92472926, 0.89359949, 0.89257866, 0.20357195],
       [0.1385965 , 0.71521344, 0.20493762, 0.13813892, 0.99753044,
        0.91853471, 0.08381696, 0.95861014, 0.8109227 , 0.81507214],
       [0.51460843, 0.89290594, 0.04652566, 0.47213124, 0.48867992,
        0.71931986, 0.72783121, 0.71234617, 0.39826849, 0.17718606],
       [0.50750503, 0.69075653, 0.5689966

In [17]:
mC = mA + mB

In [18]:
mD = mA * mB

Connected to .conda (Python 3.9.19)

In [1]:
import os
# import sys
# import IPython
import pandas as pd

In [2]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [3]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [4]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


<ipython-input-4-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


In [5]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [6]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

# dfTads = dfTads0.query('CompanyName == companyNamesVelo')
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Commonwealth Edison Co', 'Northern Municipal Power Agency', 'Undetermined Company', 'AmerenIP', 'American Transmission Co LLC', 'Northern Indiana Public Service Co LLC'}
Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Commonwealth Edison Company', 'Ameren Services Company', 'Northern Indiana Public Service Company [BA', 'American Transmission Company'}
{'600-799 kV', '200-299 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [7]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [8]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
{"""
Checks for partial match between a row and another dataframe.

Args:
    row: A pandas Series representing a row from dfVelo.
    from_col: Name of the "From" column in dfVelo.
    to_col: Name of the "To" column in dfVelo.
    other_df: The other dataframe (dfTads).
    other_from: Name of the "From" column in dfTads.
    other_to: Name of the "To" column in dfTads.

Returns:
    A boolean indicating if there's a partial match.
"""}
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

IndentationError: expected an indented block (<ipython-input-8-01b4ffc84a2b>, line 4)

In [9]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
{"""
Checks for partial match between a row and another dataframe.

Args:
    row: A pandas Series representing a row from dfVelo.
    from_col: Name of the "From" column in dfVelo.
    to_col: Name of the "To" column in dfVelo.
    other_df: The other dataframe (dfTads).
    other_from: Name of the "From" column in dfTads.
    other_to: Name of the "To" column in dfTads.

Returns:
    A boolean indicating if there's a partial match.
"""}
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

IndentationError: expected an indented block (<ipython-input-9-01b4ffc84a2b>, line 4)

In [10]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
{"""
Checks for partial match between a row and another dataframe.

Args:
    row: A pandas Series representing a row from dfVelo.
    from_col: Name of the "From" column in dfVelo.
    to_col: Name of the "To" column in dfVelo.
    other_df: The other dataframe (dfTads).
    other_from: Name of the "From" column in dfTads.
    other_to: Name of the "To" column in dfTads.

Returns:
    A boolean indicating if there's a partial match.
"""}
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()
end
# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

IndentationError: expected an indented block (<ipython-input-10-a2af7a3e72e8>, line 4)

In [11]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
"""
Checks for partial match between a row and another dataframe.

Args:
    row: A pandas Series representing a row from dfVelo.
    from_col: Name of the "From" column in dfVelo.
    to_col: Name of the "To" column in dfVelo.
    other_df: The other dataframe (dfTads).
    other_from: Name of the "From" column in dfTads.
    other_to: Name of the "To" column in dfTads.

Returns:
    A boolean indicating if there's a partial match.
"""
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

IndentationError: expected an indented block (<ipython-input-11-5263af1ee47e>, line 4)

In [12]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):

  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [13]:
dfVelo['From Sub']

1           Belvidere
2         Marengo Tap
3         Marengo Tap
4             McHenry
5         Marengo Tap
            ...      
514    Chicago Avenue
515        Dune Acres
516           Kenwood
517          Highland
518            Roxana
Name: From Sub, Length: 459, dtype: object

In [14]:
dfVelo['To Sub']

1                   Marengo Tap
2                     Woodstock
3                       Marengo
4                  Crystal Lake
5      Pleasant Valley (Indope)
                 ...           
514            Praxair Inc No 1
515               Michigan City
516                    Highland
517                 Lake George
518                   Sheffield
Name: To Sub, Length: 459, dtype: object

In [15]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):

    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [16]:
matched_rows

NameError: name 'matched_rows' is not defined

In [17]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

In [19]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
        """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

IndentationError: unindent does not match any outer indentation level (<tokenize>, line 18)

In [21]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
        """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    
    return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

IndentationError: unindent does not match any outer indentation level (<tokenize>, line 19)

In [22]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
        """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    
return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

NameError: name 'row' is not defined

In [23]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
        """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
    
return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

NameError: name 'row' is not defined

In [25]:
# Define a function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
        """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
        
    return from_match.any() or to_match.any()

end
# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

IndentationError: unindent does not match any outer indentation level (<tokenize>, line 19)

In [26]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of the "From" column in dfTads.
      other_to: Name of the "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  
  return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

In [28]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """

  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  
  return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

IndentationError: unindent does not match any outer indentation level (<tokenize>, line 18)

In [29]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])

    return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

In [30]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])

    return from_match.any() or to_match.any()

# # Apply the function to each row in dfVelo
# matched_rows = dfVelo.apply(partial_match, axis=1, args=(
#     "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# # Filter dfVelo based on the matched rows boolean Series
# result_df = dfVelo[matched_rows]

# # Print the resulting dataframe with partial matches
# print(result_df)

In [31]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])

    return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [32]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
    to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])

    return from_match.any() or to_match.any()

# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [33]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    # Option 1: Assuming other_df[other_from] contains a single value (remove .any())
    from_match = row[from_col].str.contains(other_df[other_from]) | other_df[other_from].str.contains(row[from_col])
    
    # Option 2: Check if any value in other_df[other_to] matches using a loop
    to_match = any(row[to_col] in value for value in other_df[other_to])

    return from_match.any() or to_match


# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [34]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    # Option 1: Assuming other_df[other_from] contains a single value (remove .any())
    from_match = row[from_col].str.contains(other_df[other_from]) | other_df[other_from].str.contains(row[from_col])
    
    # Option 2: Check if any value in other_df[other_to] matches using a loop
    to_match = any(row[to_col] in value for value in other_df[other_to])

    return from_match.any() or to_match

In [35]:
# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [36]:
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
    """
    Checks for partial match between a row and another dataframe.

    Args:
        row: A pandas Series representing a row from dfVelo.
        from_col: Name of the "From" column in dfVelo.
        to_col: Name of the "To" column in dfVelo.
        other_df: The other dataframe (dfTads).
        other_from: Name of the "From" column in dfTads.
        other_to: Name of the "To" column in dfTads.

    Returns:
        A boolean indicating if there's a partial match.
    """
    
    # Assuming other_df[other_from] potentially contains multiple values
    from_match = any(row[from_col] in value for value in other_df[other_from])
    
    # Option 2: Check if any value in other_df[other_to] matches using a loop
    to_match = any(row[to_col] in value for value in other_df[other_to])

    return from_match.any() or to_match

In [37]:
# Apply the function to each row in dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))

# Filter dfVelo based on the matched rows boolean Series
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

TypeError: argument of type 'float' is not iterable

In [38]:
dfTads['FromBus']

448                ADM Faries Parkway
449                ADM Faries Parkway
2564                              NaN
2565                              NaN
2566                              NaN
                     ...             
296659    Cedar Ridge Wind Generation
296660    Cedar Ridge Wind Generation
296661                  Howards Grove
296662                  Howards Grove
296663                   Nelson Dewey
Name: FromBus, Length: 16052, dtype: object

In [39]:
type(dfTads['FromBus'])

pandas.core.series.Series

In [40]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({'From Sub': ['TRAFO A', 'B101', 'FEEDER X1'], 'To Sub': ['BUS-123', 'FEEDER Y2', 'TRAFO B']})
dfTads = pd.DataFrame({'FromBus': ['TRAFO-A', 'FEEDER-X1', 'BUS 124'], 'ToBus': ['BUS 123', 'BUS-Y2', 'TRAFO-B']})

# Function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of "From" column in dfTads.
      other_to: Name of "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function and filter dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [41]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({'From Sub': ['TRAFO A', 'B101', 'FEEDER X1'], 'To Sub': ['BUS-123', 'FEEDER Y2', 'TRAFO B']})
dfTads = pd.DataFrame({'FromBus': ['TRAFO-A', 'FEEDER-X1', 'BUS 124'], 'ToBus': ['BUS 123', 'BUS-Y2', 'TRAFO-B']})

# Function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of "From" column in dfTads.
      other_to: Name of "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function and filter dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [42]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({'From Sub': ['TRAFO A', 'B101', 'FEEDER X1'], 'To Sub': ['BUS-123', 'FEEDER Y2', 'TRAFO B']})
dfTads = pd.DataFrame({'FromBus': ['TRAFO-A', 'FEEDER-X1', 'BUS 124'], 'ToBus': ['BUS 123', 'BUS-Y2', 'TRAFO-B']})

# Function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of "From" column in dfTads.
      other_to: Name of "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  from_match = row[from_col].str.contains(other_df[other_from].any()) | other_df[other_from].str.contains(row[from_col])
  to_match = row[to_col].str.contains(other_df[other_to].any()) | other_df[other_to].str.contains(row[to_col])
  return from_match.any() or to_match.any()

# Apply the function and filter dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [43]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({'From Sub': ['TRAFO A', 'B101', 'FEEDER X1'], 'To Sub': ['BUS-123', 'FEEDER Y2', 'TRAFO B']})
dfTads = pd.DataFrame({'FromBus': ['TRAFO-A', 'FEEDER-X1', 'BUS 124'], 'ToBus': ['BUS 123', 'BUS-Y2', 'TRAFO-B']})

# Function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of "From" column in dfTads.
      other_to: Name of "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  
  # Assuming other_df[other_from] potentially contains multiple values (modify if single value)
  from_match = any(row[from_col].str.contains(value) for value in other_df[other_from])
  
  # Similar check for to_match
  to_match = any(row[to_col].str.contains(value) for value in other_df[other_to])
  
  return from_match.any() or to_match.any()


# Apply the function and filter dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [44]:
# Sample DataFrames
dfVelo = pd.DataFrame({'From Sub': ['TRAFO A', 'B101', 'FEEDER X1'], 'To Sub': ['BUS-123', 'FEEDER Y2', 'TRAFO B']})
dfTads = pd.DataFrame({'FromBus': ['TRAFO-A', 'FEEDER-X1', 'BUS 124'], 'ToBus': ['BUS 123', 'BUS-Y2', 'TRAFO-B']})

# Function to check for partial match
def partial_match(row, from_col, to_col, other_df, other_from, other_to):
  """
  Checks for partial match between a row and another dataframe.

  Args:
      row: A pandas Series representing a row from dfVelo.
      from_col: Name of the "From" column in dfVelo.
      to_col: Name of the "To" column in dfVelo.
      other_df: The other dataframe (dfTads).
      other_from: Name of "From" column in dfTads.
      other_to: Name of "To" column in dfTads.

  Returns:
      A boolean indicating if there's a partial match.
  """
  # Assuming other_df[other_from] potentially contains multiple values
  from_match = any(row[from_col].str.contains(value) for value in other_df[other_from])
  
  # Similar check for to_match
  to_match = any(row[to_col].str.contains(value) for value in other_df[other_to])
  
  return from_match.any() or to_match.any()

# Apply the function and filter dfVelo
matched_rows = dfVelo.apply(partial_match, axis=1, args=(
    "From Sub", "To Sub", dfTads, "FromBus", "ToBus"))
result_df = dfVelo[matched_rows]

# Print the resulting dataframe with partial matches
print(result_df)

AttributeError: 'str' object has no attribute 'str'

In [45]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({
    'From Sub': ['BusA', 'BusB', 'BusC', 'BusD'],
    'To Sub': ['BusE', 'BusF', 'BusG', 'BusH']
})

dfTads = pd.DataFrame({
    'FromBus': ['BusA', 'BusX', 'BusC', 'BusY'],
    'ToBus': ['BusZ', 'BusF', 'BusG', 'BusH']
})

# Function to find partial matches
def find_partial_matches(df1, col1, df2, col2):
    return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# Finding partial matches
matching_rows_from_sub_to_from_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
matching_rows_from_sub_to_to_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
matching_rows_to_sub_to_from_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
matching_rows_to_sub_to_to_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# Display results
print("Matching rows from 'From Sub' to 'FromBus':")
print(matching_rows_from_sub_to_from_bus)

print("\nMatching rows from 'From Sub' to 'ToBus':")
print(matching_rows_from_sub_to_to_bus)

print("\nMatching rows from 'To Sub' to 'FromBus':")
print(matching_rows_to_sub_to_from_bus)

print("\nMatching rows from 'To Sub' to 'ToBus':")
print(matching_rows_to_sub_to_to_bus)

Matching rows from 'From Sub' to 'FromBus':
  From Sub To Sub
0     BusA   BusE
2     BusC   BusG

Matching rows from 'From Sub' to 'ToBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'FromBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'ToBus':
  From Sub To Sub
1     BusB   BusF
2     BusC   BusG
3     BusD   BusH


In [46]:
import os
# import sys
# import IPython
import pandas as pd

In [47]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [48]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [49]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-49-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [50]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [51]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Commonwealth Edison Company', 'Ameren Services Company', 'Northern Indiana Public Service Company [BA', 'American Transmission Company'}


In [52]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'600-799 kV', '200-299 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [53]:
def find_partial_matches(df1, col1, df2, col2):
    return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# Finding partial matches
matching_rows_from_sub_to_from_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
matching_rows_from_sub_to_to_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
matching_rows_to_sub_to_from_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
matching_rows_to_sub_to_to_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# Display results
print("Matching rows from 'From Sub' to 'FromBus':")
print(matching_rows_from_sub_to_from_bus)

print("\nMatching rows from 'From Sub' to 'ToBus':")
print(matching_rows_from_sub_to_to_bus)

print("\nMatching rows from 'To Sub' to 'FromBus':")
print(matching_rows_to_sub_to_from_bus)

print("\nMatching rows from 'To Sub' to 'ToBus':")
print(matching_rows_to_sub_to_to_bus)

<ipython-input-53-7d8c39e59785>:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]


Matching rows from 'From Sub' to 'FromBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'From Sub' to 'ToBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'FromBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'ToBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []


In [54]:
def find_partial_matches(df1, col1, df2, col2):
    return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# Finding partial matches
matching_rows_from_sub_to_from_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
matching_rows_from_sub_to_to_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
matching_rows_to_sub_to_from_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
matching_rows_to_sub_to_to_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# Display results
print("Matching rows from 'From Sub' to 'FromBus':")
print(matching_rows_from_sub_to_from_bus)

print("\nMatching rows from 'From Sub' to 'ToBus':")
print(matching_rows_from_sub_to_to_bus)

print("\nMatching rows from 'To Sub' to 'FromBus':")
print(matching_rows_to_sub_to_from_bus)

print("\nMatching rows from 'To Sub' to 'ToBus':")
print(matching_rows_to_sub_to_to_bus)

Matching rows from 'From Sub' to 'FromBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'From Sub' to 'ToBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'FromBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

Matching rows from 'To Sub' to 'ToBus':
Empty DataFrame
Columns: [From Sub, To Sub]
Index: []


<ipython-input-54-7d8c39e59785>:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]


In [55]:
dfVelo[dfVelo['From Sub'] == "Collins"]

Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

In [56]:
serachDf = dfVelo[dfVelo['From Sub'] == "Collins"]

In [57]:
searheddf = dfVelo[dfVelo['From Sub'] == "Collins"]

In [58]:
size(serachDf)

NameError: name 'size' is not defined

In [59]:
searcheddf = dfVelo[dfVelo['From Sub'] == "Collins"]

In [60]:
searcheddf.size

0

In [61]:
serachDf = dfVelo[dfVelo['From Sub'] == "McHenry"]

In [62]:
searchVelo = dfVelo[dfVelo['From Sub'] == "McHenry"]

In [63]:
searchVelo

Empty DataFrame
Columns: [From Sub, To Sub]
Index: []

In [64]:
dfVelo

From Sub To Sub
0     BusA   BusE
1     BusB   BusF
2     BusC   BusG
3     BusD   BusH

In [65]:
import os
# import sys
# import IPython
import pandas as pd

In [66]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [67]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [68]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-68-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [69]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [70]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Commonwealth Edison Co', 'Northern Municipal Power Agency', 'Undetermined Company', 'AmerenIP', 'American Transmission Co LLC', 'Northern Indiana Public Service Co LLC'}


In [71]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Commonwealth Edison Company', 'Ameren Services Company', 'Northern Indiana Public Service Company [BA', 'American Transmission Company'}


In [72]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'600-799 kV', '200-299 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [73]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [74]:
def find_partial_matches(df1, col1, df2, col2):
    return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# Finding partial matches
matching_rows_from_sub_to_from_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
matching_rows_from_sub_to_to_bus = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
matching_rows_to_sub_to_from_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
matching_rows_to_sub_to_to_bus = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# Display results
print("Matching rows from 'From Sub' to 'FromBus':")
print(matching_rows_from_sub_to_from_bus)

print("\nMatching rows from 'From Sub' to 'ToBus':")
print(matching_rows_from_sub_to_to_bus)

print("\nMatching rows from 'To Sub' to 'FromBus':")
print(matching_rows_to_sub_to_from_bus)

print("\nMatching rows from 'To Sub' to 'ToBus':")
print(matching_rows_to_sub_to_to_bus)

Matching rows from 'From Sub' to 'FromBus':
                               Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16         

<ipython-input-74-7d8c39e59785>:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]


In [75]:
matching_rows_from_sub_to_from_bus

Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16                       Mazon to Dresden 138 138 kV     NaN         138   
..                                               ...     ...         ...   
512                        Marktown to LTV #2 138 kV     NaN         138   
514        Chicago Avenue to Praxair Inc No 1 138 kV     NaN         138   
515               Dune Acres to Michigan City 345 kV     NaN         345   
517                   Highland to Lake George 138 kV     NaN         138   
518                       Roxana to Sheffield 138 kV     NaN         138   

    Voltage Class kV  Number of Lines    Proposed Underground  \
1            100-161                2  In Service           F   
7            100-161                2  In Service           F   
11           100-161                1  In Service           F   
12           100-161                1  In Service           F   
16           100-161                1  In Service           F   
..               ...              ...         ...         ...   
512          100-161                1  In Service           F   
514          100-161                1  In Service           F   
515              345                1  In Service           F   
517          100-161                1  In Service           F   
518          100-161                1  In Service           F   

                     From Sub            To Sub  ...  Length mi  \
1                   Belvidere       Marengo Tap  ...  12.579538   
7    Pleasant Valley (Indope)      Crystal Lake  ...   7.177511   
11                   W Dekalb           Glidden  ...   5.922115   
12            West Dekalb Tap          W Dekalb  ...  10.375795   
16                      Mazon       Dresden 138  ...  16.454078   
..                        ...               ...  ...        ...   
512                  Marktown            LTV #2  ...   0.590847   
514            Chicago Avenue  Praxair Inc No 1  ...   2.533518   
515                Dune Acres     Michigan City  ...  11.776760   
517                  Highland       Lake George  ...  11.143082   
518                    Roxana         Sheffield  ...   4.833556   

     Location Code          Source Numeric Voltages  \
1                1  Aerial Imagery          100-161   
7                1  Aerial Imagery          100-161   
11               1  Aerial Imagery          100-161   
12               1  Aerial Imagery          100-161   
16               1  Aerial Imagery          100-161   
..             ...             ...              ...   
512              1  Aerial Imagery          100-161   
514              1  Aerial Imagery          100-161   
515              1  Aerial Imagery              345   
517              1  Aerial Imagery          100-161   
518              1  Aerial Imagery          100-161   

                Holding Company Name Owner2 ID  Rec_ID  Layer_ID  Type  \
1                        Exelon Corp       -99    2732        82    AC   
7                        Exelon Corp       -99    2738        82    AC   
11                       Exelon Corp       -99   60419        82    AC   
12        

In [76]:
def find_partial_matches(df1, col1, df2, col2):
    return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# Finding partial matches
matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# Display results
print("Matching rows from 'From Sub' to 'FromBus':")
print(matchV1T1)

print("\nMatching rows from 'From Sub' to 'ToBus':")
print(matchV1T2)

print("\nMatching rows from 'To Sub' to 'FromBus':")
print(matchV2T1)

print("\nMatching rows from 'To Sub' to 'ToBus':")
print(matchV2T2)

Matching rows from 'From Sub' to 'FromBus':
                               Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16         

<ipython-input-76-ce69598a7dba>:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]


In [77]:
matchedInOrder = matchV1T1.loc[matchV2T2.index]  # Equivalent to df2.loc[df1.index]


KeyError: '[2, 3, 4, 5, 6, 8, 9, 10, 13, 14, 15, 19, 20, 25, 30, 36, 37, 68, 69, 75, 77, 78, 80, 81, 82, 84, 85, 87, 89, 90, 91, 97, 99, 100, 101, 102, 103, 104, 106, 108, 110, 112, 113, 115, 118, 120, 125, 133, 135, 136, 139, 140, 141, 144, 147, 148, 152, 155, 157, 158, 159, 161, 162, 163, 164, 167, 171, 172, 173, 174, 176, 179, 181, 182, 184, 186, 187, 188, 191, 192, 193, 194, 195, 196, 197, 198, 200, 202, 204, 205, 206, 207, 210, 211, 212, 213, 215, 216, 218, 219, 247, 250, 251, 252, 253, 254, 257, 258, 259, 260, 261, 265, 268, 269, 271, 273, 275, 280, 285, 286, 288, 290, 291, 292, 293, 295, 296, 297, 298, 299, 300, 302, 304, 308, 309, 315, 317, 318, 319, 320, 321, 322, 323, 326, 339, 340, 341, 347, 348, 356, 360, 361, 364, 369, 370, 375, 379, 384, 386, 396, 397, 399, 400, 401, 403, 404, 406, 407, 414, 433, 434, 438, 440, 445, 447, 452, 454, 456, 458, 459, 460, 461, 462, 464, 468, 472, 477, 482, 483, 484, 488, 491, 492, 494, 497, 501, 503, 504, 505, 511, 513, 516] not in index'

In [78]:
# Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

intersection_df = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# Print the intersection DataFrame
print("Intersection of matchV1T1 and matchV2T2:")
print(intersection_df)


Intersection of matchV1T1 and matchV2T2:
                               Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16            

In [79]:
# Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# Print the intersection DataFrame
print("Intersection of matchV1T1 and matchV2T2:")
print(intersection_V1T1_V2T2)

Intersection of matchV1T1 and matchV2T2:
                               Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16            

In [80]:
intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# Print the intersection DataFrame
print("Intersection of matchV1T2 and matchV2T1:")
print(intersection_V1T2_V2T1)

Intersection of matchV1T2 and matchV2T1:
                               Company Name  \
5                    Commonwealth Edison Co   
6                    Commonwealth Edison Co   
8                    Commonwealth Edison Co   
9                    Commonwealth Edison Co   
10                   Commonwealth Edison Co   
..                                      ...   
513  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
516         Northern Municipal Power Agency   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                             Transmission Line Name  Owner2  Voltage kV  \
5    Marengo Tap to Pleasant Valley (Indope) 138 kV     NaN         138   
6      Woodstock to Pleasant Valley (Indope) 138 kV     NaN         138   
8      Algonquin to Pleasant Valley (Indope) 138 kV     NaN         138   
9                        Glidden to Waterman 138 kV     NaN         138   
10                 

In [81]:
intersection_V1T2_V2T1

Company Name  \
5                    Commonwealth Edison Co   
6                    Commonwealth Edison Co   
8                    Commonwealth Edison Co   
9                    Commonwealth Edison Co   
10                   Commonwealth Edison Co   
..                                      ...   
513  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
516         Northern Municipal Power Agency   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                             Transmission Line Name  Owner2  Voltage kV  \
5    Marengo Tap to Pleasant Valley (Indope) 138 kV     NaN         138   
6      Woodstock to Pleasant Valley (Indope) 138 kV     NaN         138   
8      Algonquin to Pleasant Valley (Indope) 138 kV     NaN         138   
9                        Glidden to Waterman 138 kV     NaN         138   
10                      Sandwich to Waterman 138 kV     NaN         138   
..                                              ...     ...         ...   
513                         LTV #2 to Roxana 138 kV     NaN         138   
515              Dune Acres to Michigan City 345 kV     NaN         345   
516                      Kenwood to Highland 138 kV     NaN         138   
517                  Highland to Lake George 138 kV     NaN         138   
518                      Roxana to Sheffield 138 kV     NaN         138   

    Voltage Class kV  Number of Lines    Proposed Underground     From Sub  \
5            100-161                2  In Service           F  Marengo Tap   
6            100-161                1  In Service           F    Woodstock   
8            100-161                2  In Service           F    Algonquin   
9            100-161                1  In Service           F      Glidden   
10           100-161                1  In Service           F     Sandwich   
..               ...              ...         ...         ...          ...   
513          100-161                1  In Service           F       LTV #2   
515              345                1  In Service           F   Dune Acres   
516          100-161                1  In Service           F      Kenwood   
517          100-161                1  In Service           F     Highland   
518          100-161                1  In Service           F       Roxana   

                       To Sub  ...  Length mi  Location Code  \
5    Pleasant Valley (Indope)  ...  10.764849              1   
6    Pleasant Valley (Indope)  ...   3.769519              1   
8    Pleasant Valley (Indope)  ...  11.096842              3   
9                    Waterman  ...   9.064341              1   
10                   Waterman  ...  15.428630              1   
..                        ...  ...        ...            ...   
513                    Roxana  ...   4.111881              1   
515             Michigan City  ...  11.776760              1   
516                  Highland  ...   1.736390              1   
517               Lake George  ...  11.143082              1   
518                 Sheffield  ...   4.833556              1   

                    Source Numeric Voltages             Holding Company Name  \
5           Aerial Imagery          100-161                      Exelon Corp   
6           Aerial Imagery          100-161                      Exelon Corp   
8    Regional Digital Data          100-161                      Exelon Corp   
9           Aerial Imagery          100-161                      Exelon Corp   
10          Aerial Imagery          100-161                      Exelon Corp   
..                     ...              ...                              ...   
513         Aerial Imagery          100-161                     NiSource Inc   
515         Aerial Imagery              345                     NiSource Inc   
516         Aerial Imagery          100-161  Northern Municipal Power Agency   
517         Aerial Imagery          100-161  Northern Munic

In [82]:
matchV1T1

Company Name  \
1                    Commonwealth Edison Co   
7                    Commonwealth Edison Co   
11                   Commonwealth Edison Co   
12                   Commonwealth Edison Co   
16                   Commonwealth Edison Co   
..                                      ...   
512  Northern Indiana Public Service Co LLC   
514  Northern Indiana Public Service Co LLC   
515  Northern Indiana Public Service Co LLC   
517         Northern Municipal Power Agency   
518         Northern Municipal Power Agency   

                              Transmission Line Name  Owner2  Voltage kV  \
1                    Belvidere to Marengo Tap 138 kV     NaN         138   
7    Pleasant Valley (Indope) to Crystal Lake 138 kV     NaN         138   
11                        W Dekalb to Glidden 138 kV     NaN         138   
12                West Dekalb Tap to W Dekalb 138 kV     NaN         138   
16                       Mazon to Dresden 138 138 kV     NaN         138   
..                                               ...     ...         ...   
512                        Marktown to LTV #2 138 kV     NaN         138   
514        Chicago Avenue to Praxair Inc No 1 138 kV     NaN         138   
515               Dune Acres to Michigan City 345 kV     NaN         345   
517                   Highland to Lake George 138 kV     NaN         138   
518                       Roxana to Sheffield 138 kV     NaN         138   

    Voltage Class kV  Number of Lines    Proposed Underground  \
1            100-161                2  In Service           F   
7            100-161                2  In Service           F   
11           100-161                1  In Service           F   
12           100-161                1  In Service           F   
16           100-161                1  In Service           F   
..               ...              ...         ...         ...   
512          100-161                1  In Service           F   
514          100-161                1  In Service           F   
515              345                1  In Service           F   
517          100-161                1  In Service           F   
518          100-161                1  In Service           F   

                     From Sub            To Sub  ...  Length mi  \
1                   Belvidere       Marengo Tap  ...  12.579538   
7    Pleasant Valley (Indope)      Crystal Lake  ...   7.177511   
11                   W Dekalb           Glidden  ...   5.922115   
12            West Dekalb Tap          W Dekalb  ...  10.375795   
16                      Mazon       Dresden 138  ...  16.454078   
..                        ...               ...  ...        ...   
512                  Marktown            LTV #2  ...   0.590847   
514            Chicago Avenue  Praxair Inc No 1  ...   2.533518   
515                Dune Acres     Michigan City  ...  11.776760   
517                  Highland       Lake George  ...  11.143082   
518                    Roxana         Sheffield  ...   4.833556   

     Location Code          Source Numeric Voltages  \
1                1  Aerial Imagery          100-161   
7                1  Aerial Imagery          100-161   
11               1  Aerial Imagery          100-161   
12               1  Aerial Imagery          100-161   
16               1  Aerial Imagery          100-161   
..             ...             ...              ...   
512              1  Aerial Imagery          100-161   
514              1  Aerial Imagery          100-161   
515              1  Aerial Imagery              345   
517              1  Aerial Imagery          100-161   
518              1  Aerial Imagery          100-161   

                Holding Company Name Owner2 ID  Rec_ID  Layer_ID  Type  \
1                        Exelon Corp       -99    2732        82    AC   
7                        Exelon Corp       -99    2738        82    AC   
11                       Exelon Corp       -99   60419        82    AC   
12        

In [84]:
matchT1V1 = find_partial_matches(dfTads, 'FromBus', dfVelo, 'From Sub')


<ipython-input-76-ce69598a7dba>:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]


In [85]:
dfVelo[1:10]

Company Name                           Transmission Line Name  \
2   Commonwealth Edison Co                  Marengo Tap to Woodstock 138 kV   
3   Commonwealth Edison Co                    Marengo Tap to Marengo 138 kV   
4   Commonwealth Edison Co                   McHenry to Crystal Lake 138 kV   
5   Commonwealth Edison Co   Marengo Tap to Pleasant Valley (Indope) 138 kV   
6   Commonwealth Edison Co     Woodstock to Pleasant Valley (Indope) 138 kV   
7   Commonwealth Edison Co  Pleasant Valley (Indope) to Crystal Lake 138 kV   
8   Commonwealth Edison Co     Algonquin to Pleasant Valley (Indope) 138 kV   
9   Commonwealth Edison Co                       Glidden to Waterman 138 kV   
10  Commonwealth Edison Co                      Sandwich to Waterman 138 kV   

    Owner2  Voltage kV Voltage Class kV  Number of Lines    Proposed  \
2      NaN         138          100-161                1  In Service   
3      NaN         138          100-161                2  In Service   
4      NaN         138          100-161                2  In Service   
5      NaN         138          100-161                2  In Service   
6      NaN         138          100-161                1  In Service   
7      NaN         138          100-161                2  In Service   
8      NaN         138          100-161                2  In Service   
9      NaN         138          100-161                1  In Service   
10     NaN         138          100-161                1  In Service   

   Underground                  From Sub                    To Sub  ...  \
2            F               Marengo Tap                 Woodstock  ...   
3            F               Marengo Tap                   Marengo  ...   
4            F                   McHenry              Crystal Lake  ...   
5            F               Marengo Tap  Pleasant Valley (Indope)  ...   
6            F                 Woodstock  Pleasant Valley (Indope)  ...   
7            F  Pleasant Valley (Indope)              Crystal Lake  ...   
8            F                 Algonquin  Pleasant Valley (Indope)  ...   
9            F                   Glidden                  Waterman  ...   
10           F                  Sandwich                  Waterman  ...   

    Length mi  Location Code                 Source Numeric Voltages  \
2   11.489827              1         Aerial Imagery          100-161   
3    1.109239              1         Aerial Imagery          100-161   
4    5.882206              1         Aerial Imagery          100-161   
5   10.764849              1         Aerial Imagery          100-161   
6    3.769519              1         Aerial Imagery          100-161   
7    7.177511              1         Aerial Imagery          100-161   
8   11.096842              3  Regional Digital Data          100-161   
9    9.064341              1         Aerial Imagery          100-161   
10  15.428630              1         Aerial Imagery          100-161   

   Holding Company Name Owner2 ID  Rec_ID  Layer_ID  Type Ownership Type  
2           Exelon Corp       -99    2737        82    AC            IOU  
3           Exelon Corp       -99   55455        82    AC            IOU  
4           Exelon Corp       -99   55456        82    AC            IOU  
5           Exelon Corp       -99   59314        82    AC            IOU  
6           Exelon Corp       -99   60845        82    AC            IOU  
7           Exelon Corp       -99    2738        82    AC            IOU  
8           Exelon Corp       -99   60896        82    AC            IOU  
9           Exelon Corp       -99    2684        82    AC            IOU  
10          Exelon Corp       -99   55454        82    AC            IOU  

[9 rows x 21 columns]

In [86]:
import pandas as pd

# Sample DataFrames
dfVelo = pd.DataFrame({
    'From Sub': ['BusA', 'BusB', 'BusC', 'BusD'],
    'To Sub': ['BusE', 'BusF', 'BusG', 'BusH']
})

dfTads = pd.DataFrame({
    'FromBus': ['BusA', 'BusX', 'BusC', 'BusY'],
    'ToBus': ['BusZ', 'BusF', 'BusG', 'BusH']
})

# Function to find and display matches with verbosity
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 5

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 2 matches dfTads row 2:
From Sub    BusC
To Sub      BusG
Name: 2, dtype: object
FromBus    BusC
ToBus      BusG
Name: 2, dtype: object



In [87]:
import os
# import sys
# import IPython
import pandas as pd

In [88]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [89]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [90]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-90-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [91]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [92]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Commonwealth Edison Co', 'Northern Municipal Power Agency', 'Undetermined Company', 'AmerenIP', 'American Transmission Co LLC', 'Northern Indiana Public Service Co LLC'}


In [93]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Commonwealth Edison Company', 'Ameren Services Company', 'Northern Indiana Public Service Company [BA', 'American Transmission Company'}


In [94]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'600-799 kV', '200-299 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [95]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [96]:
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 5

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [97]:
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 5

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [98]:
exact_matches

[(10,
  Company Name                   Commonwealth Edison Co
  Transmission Line Name    Sandwich to Waterman 138 kV
  Owner2                                            NaN
  Voltage kV                                        138
  Voltage Class kV                              100-161
  Number of Lines                                     1
  Proposed                                   In Service
  Underground                                         F
  From Sub                                     Sandwich
  To Sub                                       Waterman
  Notes                                             NaN
  Length mi                                    15.42863
  Location Code                                       1
  Source                                 Aerial Imagery
  Numeric Voltages                              100-161
  Holding Company Name                      Exelon Corp
  Owner2 ID                                         -99
  Rec_ID                                  

In [99]:
size(exact_matches)

NameError: name 'size' is not defined

In [100]:
exact_matches.size

AttributeError: 'list' object has no attribute 'size'

In [101]:
exact_matches.len

AttributeError: 'list' object has no attribute 'len'

In [102]:
exact_matches.length

AttributeError: 'list' object has no attribute 'length'

In [103]:
exact_matches.size

AttributeError: 'list' object has no attribute 'size'

In [104]:
dfVelo['Voltage Class kV']

1      100-161
2      100-161
3      100-161
4      100-161
5      100-161
        ...   
514    100-161
515        345
516    100-161
517    100-161
518    100-161
Name: Voltage Class kV, Length: 459, dtype: object

In [105]:
set(dfVelo['Voltage Class kV'])

{'100-161', '345', '735 and Above'}

In [106]:
set(dfTads['Voltage Class kV'])

KeyError: 'Voltage Class kV'

In [107]:
dfTads['VoltageClassCodeName']

448       100-199 kV
449       100-199 kV
2564      200-299 kV
2565      200-299 kV
2566      200-299 kV
             ...    
296659    100-199 kV
296660    100-199 kV
296661    100-199 kV
296662    100-199 kV
296663    100-199 kV
Name: VoltageClassCodeName, Length: 16052, dtype: object

In [108]:
set(dfTads['VoltageClassCodeName'])

{'100-199 kV', '200-299 kV', '300-399 kV', '600-799 kV'}

In [109]:
set(dfTads['CompanyName'])

{'Ameren Services Company',
 'American Transmission Company',
 'Commonwealth Edison Company',
 'Northern Indiana Public Service Company [BA'}

In [110]:
set(dfVelo['Company Name'])

{'AmerenIP',
 'American Transmission Co LLC',
 'Commonwealth Edison Co',
 'Northern Indiana Public Service Co LLC',
 'Northern Municipal Power Agency',
 'Undetermined Company'}

In [111]:
import os
# import sys
# import IPython
import pandas as pd

In [112]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [113]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [114]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-114-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [115]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [116]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Commonwealth Edison Co', 'Northern Municipal Power Agency', 'Undetermined Company', 'AmerenIP', 'American Transmission Co LLC', 'Northern Indiana Public Service Co LLC'}


In [117]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Commonwealth Edison Company', 'Ameren Services Company', 'Northern Indiana Public Service Company [BA', 'American Transmission Company'}


In [118]:
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 5

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [119]:
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 100

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [120]:
def find_and_display_matches(df1, col1, df2, col2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo, 'From Sub', dfTads, 'FromBus', max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [121]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, row1, idx2, row2))
                count += 1
                print(f"Match {count}:")
                print(f"dfVelo row {idx1} matches dfTads row {idx2}:\n{row1}\n{row2}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 100

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 matches dfTads row 49016:
Company Name                   Commonwealth Edison Co
Transmission Line Name    Sandwich to Waterman 138 kV
Owner2                                            NaN
Voltage kV                                        138
Voltage Class kV                              100-161
Number of Lines                                     1
Proposed                                   In Service
Underground                                         F
From Sub                                     Sandwich
To Sub                                       Waterman
Notes                                             NaN
Length mi                                    15.42863
Location Code                                       1
Source                                 Aerial Imagery
Numeric Voltages                              100-161
Holding Company Name                      Exelon Corp
Owner2 ID                                  

In [122]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, idx2))
                count += 1
                if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
                elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 100

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49016 'FromBus': Sandwich, 'ToBus': Waterman

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49481 'FromBus': Sandwich, 'ToBus': Waterman

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49482 'FromBus': Sandwich, 'ToBus': Waterman

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 65284 'FromBus': Sandwich, 'ToBus': Waterman

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 88997 'FromBus': Sandwich, 'ToBus': Waterman

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 111212 'FromBus': Sandwich, 'ToBus': Waterman

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 131492 'FromBus': Sandwich, 'ToBus': Waterman

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 182023 'FromBus': Sandwich, 'ToB

In [123]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, idx2))
                count += 1
                if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
                elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
                if count >= max_matches:
                    return matches
    return matches

# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49016 'FromBus': Sandwich, 'ToBus': Waterman

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49481 'FromBus': Sandwich, 'ToBus': Waterman

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49482 'FromBus': Sandwich, 'ToBus': Waterman

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 65284 'FromBus': Sandwich, 'ToBus': Waterman

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 88997 'FromBus': Sandwich, 'ToBus': Waterman

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 111212 'FromBus': Sandwich, 'ToBus': Waterman

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 131492 'FromBus': Sandwich, 'ToBus': Waterman

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 182023 'FromBus': Sandwich, 'ToB

In [124]:
# Function to find and display matches with verbosity
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, idx2))
                count += 1
                if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
                elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
                match_found = True
                if count >= max_matches:
                    return matches
                break
        if match_found:
            continue
    return matches

# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 49016 'FromBus': Sandwich, 'ToBus': Waterman

Match 2:
dfVelo row 17 'From Sub': Plano, 'To Sub': Collins
dfTads row 48547 'FromBus': Plano, 'ToBus': Collins

Match 3:
dfVelo row 23 'From Sub': Dresden, 'To Sub': Collins
dfTads row 48464 'FromBus': Dresden, 'ToBus': Collins

Match 4:
dfVelo row 29 'From Sub': Cherry Valley, 'To Sub': Glidden
dfTads row 48916 'FromBus': Cherry Valley, 'ToBus': Glidden

Match 5:
dfVelo row 43 'From Sub': Zion, 'To Sub': Arcadian
dfTads row 2666 'FromBus': Zion, 'ToBus': Arcadian

Match 6:
dfVelo row 56 'From Sub': Wayne, 'To Sub': Spaulding
dfTads row 48995 'FromBus': Wayne, 'ToBus': Spaulding

Match 7:
dfVelo row 59 'From Sub': Wayne, 'To Sub': Electric Junction
dfTads row 48493 'FromBus': Wayne, 'ToBus': Electric Junction

Match 8:
dfVelo row 64 'From Sub': Itasca, 'To Sub': Lombard
dfTads row 48507 'FromBus': Itasca, 'ToBus': Lombard


In [125]:
dfVelo[1:10]

Company Name                           Transmission Line Name  \
2   Commonwealth Edison Co                  Marengo Tap to Woodstock 138 kV   
3   Commonwealth Edison Co                    Marengo Tap to Marengo 138 kV   
4   Commonwealth Edison Co                   McHenry to Crystal Lake 138 kV   
5   Commonwealth Edison Co   Marengo Tap to Pleasant Valley (Indope) 138 kV   
6   Commonwealth Edison Co     Woodstock to Pleasant Valley (Indope) 138 kV   
7   Commonwealth Edison Co  Pleasant Valley (Indope) to Crystal Lake 138 kV   
8   Commonwealth Edison Co     Algonquin to Pleasant Valley (Indope) 138 kV   
9   Commonwealth Edison Co                       Glidden to Waterman 138 kV   
10  Commonwealth Edison Co                      Sandwich to Waterman 138 kV   

    Owner2  Voltage kV Voltage Class kV  Number of Lines    Proposed  \
2      NaN         138          100-161                1  In Service   
3      NaN         138          100-161                2  In Service   
4      NaN         138          100-161                2  In Service   
5      NaN         138          100-161                2  In Service   
6      NaN         138          100-161                1  In Service   
7      NaN         138          100-161                2  In Service   
8      NaN         138          100-161                2  In Service   
9      NaN         138          100-161                1  In Service   
10     NaN         138          100-161                1  In Service   

   Underground                  From Sub                    To Sub  ...  \
2            F               Marengo Tap                 Woodstock  ...   
3            F               Marengo Tap                   Marengo  ...   
4            F                   McHenry              Crystal Lake  ...   
5            F               Marengo Tap  Pleasant Valley (Indope)  ...   
6            F                 Woodstock  Pleasant Valley (Indope)  ...   
7            F  Pleasant Valley (Indope)              Crystal Lake  ...   
8            F                 Algonquin  Pleasant Valley (Indope)  ...   
9            F                   Glidden                  Waterman  ...   
10           F                  Sandwich                  Waterman  ...   

    Length mi  Location Code                 Source Numeric Voltages  \
2   11.489827              1         Aerial Imagery          100-161   
3    1.109239              1         Aerial Imagery          100-161   
4    5.882206              1         Aerial Imagery          100-161   
5   10.764849              1         Aerial Imagery          100-161   
6    3.769519              1         Aerial Imagery          100-161   
7    7.177511              1         Aerial Imagery          100-161   
8   11.096842              3  Regional Digital Data          100-161   
9    9.064341              1         Aerial Imagery          100-161   
10  15.428630              1         Aerial Imagery          100-161   

   Holding Company Name Owner2 ID  Rec_ID  Layer_ID  Type Ownership Type  
2           Exelon Corp       -99    2737        82    AC            IOU  
3           Exelon Corp       -99   55455        82    AC            IOU  
4           Exelon Corp       -99   55456        82    AC            IOU  
5           Exelon Corp       -99   59314        82    AC            IOU  
6           Exelon Corp       -99   60845        82    AC            IOU  
7           Exelon Corp       -99    2738        82    AC            IOU  
8           Exelon Corp       -99   60896        82    AC            IOU  
9           Exelon Corp       -99    2684        82    AC            IOU  
10          Exelon Corp       -99   55454        82    AC            IOU  

[9 rows x 21 columns]

In [126]:
dfVelo['From Sub'][0:9]

1                   Belvidere
2                 Marengo Tap
3                 Marengo Tap
4                     McHenry
5                 Marengo Tap
6                   Woodstock
7    Pleasant Valley (Indope)
8                   Algonquin
9                     Glidden
Name: From Sub, dtype: object

In [127]:
companyNamesVelo2Tads

{'Ameren Services Company',
 'American Transmission Company',
 'Commonwealth Edison Company',
 'Northern Indiana Public Service Company [BA'}

Connected to .conda (Python 3.9.19)

In [1]:
import os
# import sys
# import IPython
import pandas as pd

In [2]:
try:
    fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
    wd = os.path.dirname(fileAddr)
    print("We seem to be working in a JuPyteR Notebook")
except ImportError:
    wd = os.getcwd()
    print("We seem to be working in a regular .py file")
    

# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [3]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [4]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


<ipython-input-4-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


In [5]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [6]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ] 
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [7]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [8]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [9]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [10]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)



# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [11]:
# Function to find and display matches with verbosity
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        for idx2, row2 in df2.iterrows():
            if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
               (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
                matches.append((idx1, idx2))
                count += 1
                if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
                elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
                    print(f"Match {count}:")
                    print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
                    print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
                match_found = True
                if count >= max_matches:
                    return matches
                break
        if match_found:
            continue
    return matches

# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Sandwich, 'ToBus': Waterman

Match 2:
dfVelo row 17 'From Sub': Plano, 'To Sub': Collins
dfTads row 89896 'FromBus': Plano, 'ToBus': Collins

Match 3:
dfVelo row 23 'From Sub': Dresden, 'To Sub': Collins
dfTads row 89842 'FromBus': Dresden, 'ToBus': Collins

Match 4:
dfVelo row 29 'From Sub': Cherry Valley, 'To Sub': Glidden
dfTads row 81795 'FromBus': Cherry Valley, 'ToBus': Glidden

Match 5:
dfVelo row 43 'From Sub': Zion, 'To Sub': Arcadian
dfTads row 11115 'FromBus': Zion, 'ToBus': Arcadian

Match 6:
dfVelo row 56 'From Sub': Wayne, 'To Sub': Spaulding
dfTads row 267543 'FromBus': Wayne, 'ToBus': Spaulding

Match 7:
dfVelo row 59 'From Sub': Wayne, 'To Sub': Electric Junction
dfTads row 118813 'FromBus': Wayne, 'ToBus': Electric Junction

Match 8:
dfVelo row 64 'From Sub': Itasca, 'To Sub': Lombard
dfTads row 187357 'FromBus': Itasca, 'ToBus': Lom

In [12]:
# VS: "Voltage Class kV" is among "100-161", "345", "735 and Above", 

In [13]:
matches

NameError: name 'matches' is not defined

In [14]:
exact_matches

[(10, 291656),
 (17, 89896),
 (23, 89842),
 (29, 81795),
 (43, 11115),
 (56, 267543),
 (59, 118813),
 (64, 187357),
 (65, 187313),
 (73, 184881),
 (78, 184847),
 (82, 262770),
 (83, 262810),
 (88, 267502),
 (92, 292346),
 (93, 283425),
 (116, 292096),
 (117, 184867),
 (119, 292156),
 (121, 292324),
 (122, 184879),
 (123, 300867),
 (124, 81825),
 (130, 142895),
 (131, 241378),
 (132, 109631),
 (133, 109545),
 (137, 109533),
 (138, 142897),
 (149, 185924),
 (151, 186916),
 (154, 214964),
 (155, 142871),
 (156, 186868),
 (160, 296582),
 (180, 238031),
 (181, 118800),
 (189, 186892),
 (193, 118780),
 (201, 101971),
 (213, 118712),
 (214, 118756),
 (219, 118712),
 (247, 280122),
 (248, 280080),
 (254, 68692),
 (257, 47616),
 (262, 142783),
 (272, 55721),
 (275, 162778),
 (276, 98257),
 (277, 98287),
 (279, 98327),
 (283, 286716),
 (288, 100842),
 (289, 100852),
 (305, 68601),
 (312, 92116),
 (313, 55733),
 (314, 68655),
 (316, 199462),
 (324, 144662),
 (325, 168322),
 (327, 280040),
 (334, 

In [15]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches

def find_and_display_matches(df1, df2, max_matches=5):
	matches = []
	count = 0

	for idx1, row1 in df1.iterrows():
		match_found = False
		latest_year = None
		latest_match_idx = None

		for idx2, row2 in df2.iterrows():
			if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
				(row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
				matches.append((idx1, idx2))
				count += 1

				# Check for retirement date
				if not pd.isna(row2['RetirementDate']):
					retirement_date = row2['RetirementDate'].strftime("%d %m %y")
					print(f"Retired on {retirement_date}")

				# Update if newer year is found
				if row2['ReportingYearNbr'] > latest_year or latest_year is None:
					latest_year = row2['ReportingYearNbr']
					latest_match_idx = idx2

				# Print details only for the latest year match
				if count > max_matches or idx2 == latest_match_idx:
					print(f"Match {count}:")
					print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
					print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n")
					match_found = True
				if count >= max_matches:
					return matches
				break

		if match_found:
			continue

	return matches

# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:



TypeError: '>' not supported between instances of 'int' and 'NoneType'

In [16]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches


def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None  # Initialize as None to avoid the error
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"].strftime("%d %m %y")
                    print(f"Retired on {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if row2["ReportingYearNbr"] is not None and (
                    row2["ReportingYearNbr"] > latest_year or latest_year is None
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches
                    break

        if match_found:
            continue
    return matches


# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:



TypeError: '>' not supported between instances of 'int' and 'NoneType'

In [17]:
import os
# import sys
# import IPython
import pandas as pd

In [18]:
try:
	fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
	wd = os.path.dirname(fileAddr)
	print("We seem to be working in a JuPyteR Notebook")
except ImportError:
	wd = os.getcwd()
	print("We seem to be working in a regular .py file")


# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [19]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [20]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


<ipython-input-20-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


In [21]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [22]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ]
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [23]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [24]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [25]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [26]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)


# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [27]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches


def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None  # Initialize as None to avoid the error
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"].strftime("%d %m %y")
                    print(f"Retired on {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if row2["ReportingYearNbr"] is not None and (
                    row2["ReportingYearNbr"] > latest_year or latest_year is None
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches
                    break

        if match_found:
            continue
    return matches


# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:



TypeError: '>' not supported between instances of 'int' and 'NoneType'

In [28]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches


def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None  # Initialize as None to avoid the error
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"].strftime("%d %m %y")
                    print(f"Retired on {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if (
                    pd.notnull(row2["ReportingYearNbr"])
                    and row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches
                    break

        if match_found:
            continue
    return matches


# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 17 'From Sub': Plano, 'To Sub': Collins
dfTads row 89896 'FromBus': Collins, 'ToBus': Plano, ReportingYearNbr: 2013

Match 3:
dfVelo row 23 'From Sub': Dresden, 'To Sub': Collins
dfTads row 89842 'FromBus': Collins, 'ToBus': Dresden, ReportingYearNbr: 2013

Match 4:
dfVelo row 29 'From Sub': Cherry Valley, 'To Sub': Glidden
dfTads row 81795 'FromBus': Cherry Valley, 'ToBus': Glidden, ReportingYearNbr: 2015



AttributeError: 'str' object has no attribute 'strftime'

In [29]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches


def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]  # Print the value directly
                    print(f"Retirement Date: {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if (
                    pd.notnull(row2["ReportingYearNbr"])
                    and row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches
                    break

        if match_found:
            continue
    return matches


# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 17 'From Sub': Plano, 'To Sub': Collins
dfTads row 89896 'FromBus': Collins, 'ToBus': Plano, ReportingYearNbr: 2013

Match 3:
dfVelo row 23 'From Sub': Dresden, 'To Sub': Collins
dfTads row 89842 'FromBus': Collins, 'ToBus': Dresden, ReportingYearNbr: 2013

Match 4:
dfVelo row 29 'From Sub': Cherry Valley, 'To Sub': Glidden
dfTads row 81795 'FromBus': Cherry Valley, 'ToBus': Glidden, ReportingYearNbr: 2015

Retirement Date: 12/30/22 0:00
Match 5:
dfVelo row 43 'From Sub': Zion, 'To Sub': Arcadian
dfTads row 11115 'FromBus': Arcadian, 'ToBus': Zion, ReportingYearNbr: 2016

Match 6:
dfVelo row 56 'From Sub': Wayne, 'To Sub': Spaulding
dfTads row 267543 'FromBus': Spaulding, 'ToBus': Wayne, ReportingYearNbr: 2015

Match 7:
dfVelo row 59 'From Sub': Wayne, 'To Sub': Electric Junction

In [30]:
dfTads['FromBus'] == 'Taney'

60        False
79        False
80        False
249       False
266       False
          ...  
300927    False
301080    False
301081    False
301082    False
301083    False
Name: FromBus, Length: 16052, dtype: bool

In [31]:
dfTads[dfTads['FromBus'] == 'Taney']

Empty DataFrame
Columns: [InventoryDataDetailID, InventoryDataID, CompanyName, CompanyCode, NERCID, NERCID_AliasID, ReportingYearNbr, RegionCode, SubRegionName, ElementIdentifierName, ElementIdentifierName_AliasID, FromBus, FromBus_AliasID, ToBus, ToBus_AliasID, TertiaryBus, TertiaryBus_AliasID, Miles, Miles_grp, BESExemptedFlag, NumberOfTerminals, NumberOfTerminals_grp, CircuitTypeCode, VoltageClassCodeName, ParentCode, ConductorsPerPhaseCode, OverheadGroundWireCode, InsulatorTypeCode, CableTypeCode, StructureMaterialCode, StructureTypeCode, CircuitsPerStructureCode, TerrainCode, ElevationCode, InServiceDate, RetirementDate, Comment, CreationDT, ExtractionDT, UpdateDT, DeletionDT, NERC_DataPullDT, ID_SK, Rnk, Slicer, AliasID, IsCurrent]
Index: []

[0 rows x 47 columns]

In [32]:
dfTads[dfTads['FromBus'] == "Taney"]

Empty DataFrame
Columns: [InventoryDataDetailID, InventoryDataID, CompanyName, CompanyCode, NERCID, NERCID_AliasID, ReportingYearNbr, RegionCode, SubRegionName, ElementIdentifierName, ElementIdentifierName_AliasID, FromBus, FromBus_AliasID, ToBus, ToBus_AliasID, TertiaryBus, TertiaryBus_AliasID, Miles, Miles_grp, BESExemptedFlag, NumberOfTerminals, NumberOfTerminals_grp, CircuitTypeCode, VoltageClassCodeName, ParentCode, ConductorsPerPhaseCode, OverheadGroundWireCode, InsulatorTypeCode, CableTypeCode, StructureMaterialCode, StructureTypeCode, CircuitsPerStructureCode, TerrainCode, ElevationCode, InServiceDate, RetirementDate, Comment, CreationDT, ExtractionDT, UpdateDT, DeletionDT, NERC_DataPullDT, ID_SK, Rnk, Slicer, AliasID, IsCurrent]
Index: []

[0 rows x 47 columns]

In [33]:
dfTads[:, dfTads['FromBus'] == "Taney"]

InvalidIndexError: (slice(None, None, None), 60        False
79        False
80        False
249       False
266       False
          ...  
300927    False
301080    False
301081    False
301082    False
301083    False
Name: FromBus, Length: 16052, dtype: bool)

In [34]:
dfTads[dfTads['FromBus'] == "Taney", :]

InvalidIndexError: (60        False
79        False
80        False
249       False
266       False
          ...  
300927    False
301080    False
301081    False
301082    False
301083    False
Name: FromBus, Length: 16052, dtype: bool, slice(None, None, None))

In [35]:
dfTads[dfTads['FromBus'] == "Taney"]

Empty DataFrame
Columns: [InventoryDataDetailID, InventoryDataID, CompanyName, CompanyCode, NERCID, NERCID_AliasID, ReportingYearNbr, RegionCode, SubRegionName, ElementIdentifierName, ElementIdentifierName_AliasID, FromBus, FromBus_AliasID, ToBus, ToBus_AliasID, TertiaryBus, TertiaryBus_AliasID, Miles, Miles_grp, BESExemptedFlag, NumberOfTerminals, NumberOfTerminals_grp, CircuitTypeCode, VoltageClassCodeName, ParentCode, ConductorsPerPhaseCode, OverheadGroundWireCode, InsulatorTypeCode, CableTypeCode, StructureMaterialCode, StructureTypeCode, CircuitsPerStructureCode, TerrainCode, ElevationCode, InServiceDate, RetirementDate, Comment, CreationDT, ExtractionDT, UpdateDT, DeletionDT, NERC_DataPullDT, ID_SK, Rnk, Slicer, AliasID, IsCurrent]
Index: []

[0 rows x 47 columns]

In [36]:
dfTads[dfTads['FromBus'] == "Munster"]

InventoryDataDetailID  InventoryDataID  \
210769                  24508             5143   
210770                  37245             6192   
210771                  69898             6785   
210772                 113863             9258   
210773                 113863             9258   
210774                 113863             9258   
210775                 113863             9258   
210776                 113863             9258   
210777                 113863             9258   
210778                 113863             9258   
210779                 113863             9258   
210780                 113863             9258   
210781                  69940             7594   
210782                 113905             9259   
210783                 113905             9259   
210784                 113905             9259   
210785                 113905             9259   
210786                 113905             9259   
210787                 113905             9259   
210788                 113905             9259   
210789                 113905             9259   
210790                 113905             9259   
210791                  70011             7594   
210792                 113976             9259   
210793                 113976             9259   
210794                 113976             9259   
210795                 113976             9259   
210796                 113976             9259   
210797                 113976             9259   
210798                 113976             9259   
210799                 113976             9259   
210800                 113976             9259   
210805                  70012             7594   
210806                 113977             9259   
210807                 113977             9259   
210808                 113977             9259   
210809                 113977             9259   
210810                 113977             9259   
210811                 113977             9259   
210812                 113977             9259   
210813                 113977             9259   
210814                 113977             9259   

                                        CompanyName     CompanyCode    NERCID  \
210769  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210770  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210771  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210772  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210773  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210774  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210775  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210776  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210777  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210778  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210779  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210780  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210781  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210782  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210783  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210784  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210785  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210786  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210787  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210788  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210789  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210790  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR026

In [37]:
dfTads[dfTads['FromBus'] == "Munster" && dfTads['ToBus'] == "Taney"]

SyntaxError: invalid syntax (<ipython-input-37-bb36abd4fa79>, line 1)

In [38]:
dfTads[dfTads['FromBus'] == "Munster"]

InventoryDataDetailID  InventoryDataID  \
210769                  24508             5143   
210770                  37245             6192   
210771                  69898             6785   
210772                 113863             9258   
210773                 113863             9258   
210774                 113863             9258   
210775                 113863             9258   
210776                 113863             9258   
210777                 113863             9258   
210778                 113863             9258   
210779                 113863             9258   
210780                 113863             9258   
210781                  69940             7594   
210782                 113905             9259   
210783                 113905             9259   
210784                 113905             9259   
210785                 113905             9259   
210786                 113905             9259   
210787                 113905             9259   
210788                 113905             9259   
210789                 113905             9259   
210790                 113905             9259   
210791                  70011             7594   
210792                 113976             9259   
210793                 113976             9259   
210794                 113976             9259   
210795                 113976             9259   
210796                 113976             9259   
210797                 113976             9259   
210798                 113976             9259   
210799                 113976             9259   
210800                 113976             9259   
210805                  70012             7594   
210806                 113977             9259   
210807                 113977             9259   
210808                 113977             9259   
210809                 113977             9259   
210810                 113977             9259   
210811                 113977             9259   
210812                 113977             9259   
210813                 113977             9259   
210814                 113977             9259   

                                        CompanyName     CompanyCode    NERCID  \
210769  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210770  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210771  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210772  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210773  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210774  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210775  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210776  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210777  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210778  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210779  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210780  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210781  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210782  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210783  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210784  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210785  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210786  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210787  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210788  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210789  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210790  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR026

In [39]:
dfTads[dfTads['FromBus'] == "Munster"] && dfTads[dfTads['ToBus'] == "Taney"]

SyntaxError: invalid syntax (<ipython-input-39-e403b6213a0d>, line 1)

In [40]:
dfTads[dfTads['ToBus'] == "Taney"]

InventoryDataDetailID  InventoryDataID  \
178982                  69978             7594   
178983                 113943             9259   
178984                 113943             9259   
178985                 113943             9259   
178986                 113943             9259   
178987                 113943             9259   
178988                 113943             9259   
178989                 113943             9259   
178990                 113943             9259   
178991                 113943             9259   
210805                  70012             7594   
210806                 113977             9259   
210807                 113977             9259   
210808                 113977             9259   
210809                 113977             9259   
210810                 113977             9259   
210811                 113977             9259   
210812                 113977             9259   
210813                 113977             9259   
210814                 113977             9259   

                                        CompanyName     CompanyCode    NERCID  \
178982  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178983  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178984  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178985  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178986  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178987  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178988  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178989  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178990  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
178991  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210805  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210806  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210807  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210808  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210809  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210810  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210811  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210812  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210813  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210814  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   

                            NERCID_AliasID  ReportingYearNbr RegionCode  \
178982  0x294791EC91004582F3E1DB12ADA4BB03              2015        RFC   
178983  0x294791EC91004582F3E1DB12ADA4BB03              2016        RFC   
178984  0x294791EC91004582F3E1DB12ADA4BB03              2017        RFC   
178985  0x294791EC91004582F3E1DB12ADA4BB03              2018        RFC   
178986  0x294791EC91004582F3E1DB12ADA4BB03              2019        RFC   
178987  0x294791EC91004582F3E1DB12ADA4BB03              2020        RFC   
178988  0x294791EC91004582F3E1DB12ADA4BB03              2021        RFC   
178989  0x294791EC91004582F3E1DB12ADA4BB03              2022        RFC   
178990  0x294791EC91004582F3E1DB12ADA4BB03              2023        RFC   
178991  0x294791EC91004582F3E1DB12ADA4BB03              2024        RFC   
210805  0x294791EC91004582F3E1DB12ADA4BB03              2015        RFC   
210806  0x294791EC91004582F3E1DB12ADA4BB03              2016        RFC   
210807  0x294791EC91004582F3E1DB12ADA4BB03              2017        RFC   
210808  0x294791EC91004582F3E1DB12ADA4BB03              2018        RFC   
210809  0x294791EC91004582F3E1DB12ADA4BB03              2019        RFC   
210810  0x294791EC91004582F3E1DB12ADA4BB03             

In [41]:
filtered_df = dfTads[(dfTads['FromBus'] == "Munster") & (dfTads['ToBus'] == "Taney")]

In [42]:
dfTads[(dfTads['FromBus'] == "Munster") & (dfTads['ToBus'] == "Taney")]

InventoryDataDetailID  InventoryDataID  \
210805                  70012             7594   
210806                 113977             9259   
210807                 113977             9259   
210808                 113977             9259   
210809                 113977             9259   
210810                 113977             9259   
210811                 113977             9259   
210812                 113977             9259   
210813                 113977             9259   
210814                 113977             9259   

                                        CompanyName     CompanyCode    NERCID  \
210805  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210806  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210807  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210808  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210809  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210810  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210811  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210812  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210813  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   
210814  Northern Indiana Public Service Company [BA  NCR02611 | RFC  NCR02611   

                            NERCID_AliasID  ReportingYearNbr RegionCode  \
210805  0x294791EC91004582F3E1DB12ADA4BB03              2015        RFC   
210806  0x294791EC91004582F3E1DB12ADA4BB03              2016        RFC   
210807  0x294791EC91004582F3E1DB12ADA4BB03              2017        RFC   
210808  0x294791EC91004582F3E1DB12ADA4BB03              2018        RFC   
210809  0x294791EC91004582F3E1DB12ADA4BB03              2019        RFC   
210810  0x294791EC91004582F3E1DB12ADA4BB03              2020        RFC   
210811  0x294791EC91004582F3E1DB12ADA4BB03              2021        RFC   
210812  0x294791EC91004582F3E1DB12ADA4BB03              2022        RFC   
210813  0x294791EC91004582F3E1DB12ADA4BB03              2023        RFC   
210814  0x294791EC91004582F3E1DB12ADA4BB03              2024        RFC   

       SubRegionName ElementIdentifierName  ... CreationDT ExtractionDT  \
210805           RFC                138095  ...    27:03.3      55:11.3   
210806           RFC                138095  ...    59:52.2      55:11.3   
210807           RFC                138095  ...    59:52.2      00:02.3   
210808           RFC                138095  ...    59:52.2      20:04.4   
210809           RFC                138095  ...    59:52.2      55:02.6   
210810           RFC                138095  ...    59:52.2      10:09.3   
210811           RFC                138095  ...    59:52.2      05:15.6   
210812           RFC                138095  ...    59:52.2      05:09.6   
210813           RFC                138095  ...    59:52.2      05:09.2   
210814           RFC                138095  ...    59:52.2      05:07.9   

       UpdateDT DeletionDT NERC_DataPullDT   ID_SK Rnk                Slicer  \
210805  27:15.4        NaN         00:20.1  136626   1   7594 | 70012 | 2015   
210806  00:19.4        NaN         00:20.1  159828   1  9259 | 113977 | 2016   
210807  56:33.3        NaN         00:00.5  199455   1  9259 | 113977 | 2017   
210808  15:36.0        NaN         00:01.1  262189   1  9259 | 113977 | 2018   
210809  52:04.3        NaN         00:01.1  326683   1  9259 | 113977 | 2019   
210810  07:32.0        NaN         04:08.8  379057   1  9259 | 113977 | 2020   
210811  00:02.1        NaN         03:26.9  388364   1  9259 | 113977 | 2021   
210812  02:23.2        NaN         01:11.3  500845   1  9259 | 113977 | 2022   
210813  00:01.0        NaN         01:16.2  543244   1  9259 | 113977 | 2023   
210814  00:01.0        NaN         01:21.7  636821   1  9259 | 113977 | 2024   

                                

In [43]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches


def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]  # Print the value directly
                    print(f"Retirement Date: {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if (
                    pd.notnull(row2["ReportingYearNbr"])
                    and row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches


# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2016

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2017

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2018

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2019

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2020

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 29166

In [44]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    seen_pairs = set()  # Track already seen bus pairs

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            # Check for matching buses and avoid duplicates
            bus_pair = (
                (row1["From Sub"], row1["To Sub"])
                if row1["From Sub"] < row1["To Sub"]
                else (row1["To Sub"], row1["From Sub"])
            )
            if bus_pair in seen_pairs:
                continue

            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                seen_pairs.add(bus_pair)  # Mark this bus pair as seen
                count = len(matches)  # Update count based on total matches

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]  # Print the value directly
                    print(f"Retirement Date: {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match
                if count > max_matches or idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [46]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    seen_pairs = set()  # Track already seen bus pairs

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            # Check for matching buses and avoid duplicates (considering order)
            bus_pair = (
                (row1["From Sub"], row1["To Sub"])
                if row1["From Sub"] < row1["To Sub"]
                else (row1["To Sub"], row1["From Sub"])
            )
            if bus_pair in seen_pairs:
                continue
            seen_pairs.add(bus_pair)  # Mark this bus pair as seen

            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count = len(matches)  # Update count based on total matches

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]  # Print the value directly
                    print(f"Retirement Date: {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match within the pair
                if idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [48]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    seen_pairs = set()  # Track already seen bus pairs

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            # Check for matching buses and avoid duplicates (considering order)
            bus_pair = (
                (row1["From Sub"], row1["To Sub"])
                if row1["From Sub"] < row1["To Sub"]
                else (row1["To Sub"], row1["From Sub"])
            )
            if bus_pair in seen_pairs:
                continue
            seen_pairs.add(bus_pair)  # Mark this bus pair as seen

            # Print bus_pair for inspection (optional for debugging)
            # print(f"Checking bus pair: {bus_pair}")

            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count = len(matches)  # Update count based on total matches

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]  # Print the value directly
                    print(f"Retirement Date: {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details only for the latest year match within the pair
                if idx2 == latest_match_idx:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [50]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"].strftime("%d %m %y")
                    print(f"Retired on {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details for all matches (up to max_matches)
                if count <= max_matches:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [52]:
import os
# import sys
# import IPython
import pandas as pd

In [53]:
try:
	fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
	wd = os.path.dirname(fileAddr)
	print("We seem to be working in a JuPyteR Notebook")
except ImportError:
	wd = os.getcwd()
	print("We seem to be working in a regular .py file")


# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [54]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [55]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-55-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [56]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [57]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ]
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [58]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [59]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [60]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [61]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)


# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [62]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches

In [63]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"].strftime("%d %m %y")
                    print(f"Retired on {retirement_date}")

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details for all matches (up to max_matches)
                if count <= max_matches:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [64]:
# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2016

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2017

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2018

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2019

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2020

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 29166

AttributeError: 'str' object has no attribute 'strftime'

In [65]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date and print directly
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]
                    print(
                        f"dfTads row {idx2}: Retired on {retirement_date}"
                    )  # Print at the end

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details for all matches (up to max_matches)
                if count <= max_matches:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [66]:
# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2016

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2017

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2018

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2019

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2020

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 29166

In [67]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    latest_year = None
    latest_match_idx = None

    for idx1, row1 in df1.iterrows():
        match_found = False

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))

                # Check for retirement date and print directly
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]
                    print(
                        f"dfTads row {idx2}: Retired on {retirement_date}"
                    )  # Print at the end

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2
                    match_found = True  # Set match found after updating latest year

        # Print only after finding the latest year for this pair (or exceeding max_matches)
        if match_found and (
            len(matches) <= max_matches or latest_match_idx is not None
        ):
            count = len(matches)
            print(f"Match {count}:")
            print(
                f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
            )
            print(
                f"dfTads row {latest_match_idx} 'FromBus': {df2.loc[latest_match_idx, 'FromBus']}, 'ToBus': {df2.loc[latest_match_idx, 'ToBus']}, ReportingYearNbr: {latest_year}\n"
            )

    return matches

In [69]:
def find_and_display_matches(df1, df2, max_matches=5):
    matches = []
    count = 0

    for idx1, row1 in df1.iterrows():
        match_found = False
        latest_year = None
        latest_match_idx = None

        for idx2, row2 in df2.iterrows():
            if (
                row1["From Sub"] == row2["FromBus"] and row1["To Sub"] == row2["ToBus"]
            ) or (
                row1["From Sub"] == row2["ToBus"] and row1["To Sub"] == row2["FromBus"]
            ):
                matches.append((idx1, idx2))
                count += 1

                # Check for retirement date and print directly
                if not pd.isna(row2["RetirementDate"]):
                    retirement_date = row2["RetirementDate"]
                    print(
                        f"dfTads row {idx2}: Retired on {retirement_date}"
                    )  # Print at the end

                # Update if a valid year is found (avoid NoneType comparison)
                if pd.notnull(row2["ReportingYearNbr"]) and (
                    row2["ReportingYearNbr"] > latest_year
                    if latest_year is not None
                    else True
                ):
                    latest_year = row2["ReportingYearNbr"]
                    latest_match_idx = idx2

                # Print details for all matches (up to max_matches)
                if count <= max_matches:
                    print(f"Match {count}:")
                    print(
                        f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                    )
                    print(
                        f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}, ReportingYearNbr: {row2['ReportingYearNbr']}\n"
                    )
                    match_found = True
                    if count >= max_matches:
                        return matches

        if match_found:
            continue
    return matches

In [70]:
# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2015

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2016

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2017

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2018

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2019

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich, ReportingYearNbr: 2020

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 29166

In [71]:
import os


def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []
    latest_year = None
    latest_match_idx = None

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))

                    # Check for retirement date and print directly
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        f.write(
                            f"dfTads row {idx2}: Retired on {retirement_date}\n"
                        )  # Print to file

                    # Update if a valid year is found (avoid NoneType comparison)
                    if pd.notnull(row2["ReportingYearNbr"]) and (
                        row2["ReportingYearNbr"] > latest_year
                        if latest_year is not None
                        else True
                    ):
                        latest_year = row2["ReportingYearNbr"]
                        latest_match_idx = idx2
                        match_found = True  # Set match found after updating latest year

            # Print only after finding the latest year for this pair (or exceeding max_matches)
            if match_found and (
                len(matches) <= max_matches or latest_match_idx is not None
            ):
                count = len(matches)
                f.write(f"Match {count}:\n")
                f.write(
                    f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                )
                f.write(
                    f"dfTads row {latest_match_idx} 'FromBus': {df2.loc[latest_match_idx, 'FromBus']}, 'ToBus': {df2.loc[latest_match_idx, 'ToBus']}, ReportingYearNbr: {latest_year}\n\n"
                )

    return matches

In [72]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []
    latest_year = None
    latest_match_idx = None

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))

                    # Check for retirement date and print directly
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        f.write(
                            f"dfTads row {idx2}: Retired on {retirement_date}\n"
                        )  # Print to file

                    # Update if a valid year is found (avoid NoneType comparison)
                    if pd.notnull(row2["ReportingYearNbr"]) and (
                        row2["ReportingYearNbr"] > latest_year
                        if latest_year is not None
                        else True
                    ):
                        latest_year = row2["ReportingYearNbr"]
                        latest_match_idx = idx2
                        match_found = True  # Set match found after updating latest year

            # Print only after finding the latest year for this pair (or exceeding max_matches)
            if match_found and (
                len(matches) <= max_matches or latest_match_idx is not None
            ):
                count = len(matches)
                f.write(f"Match {count}:\n")
                f.write(
                    f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                )
                f.write(
                    f"dfTads row {latest_match_idx} 'FromBus': {df2.loc[latest_match_idx, 'FromBus']}, 'ToBus': {df2.loc[latest_match_idx, 'ToBus']}, ReportingYearNbr: {latest_year}\n\n"
                )

    return matches

In [74]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []
    latest_year = None
    latest_match_idx = None

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))

                    # Check for retirement date
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(
                            f"dfTads row {idx2}: Retired on {retirement_date}"
                        )  # Print to terminal
                        f.write(
                            f"dfTads row {idx2}: Retired on {retirement_date}\n"
                        )  # Write to file

                    # Update if a valid year is found (avoid NoneType comparison)
                    if pd.notnull(row2["ReportingYearNbr"]) and (
                        row2["ReportingYearNbr"] > latest_year
                        if latest_year is not None
                        else True
                    ):
                        latest_year = row2["ReportingYearNbr"]
                        latest_match_idx = idx2
                        match_found = True  # Set match found after updating latest year

            # Print only after finding the latest year for this pair (or exceeding max_matches)
            if match_found and (
                len(matches) <= max_matches or latest_match_idx is not None
            ):
                count = len(matches)
                print(f"Match {count}:")
                print(
                    f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                )
                print(
                    f"dfTads row {latest_match_idx} 'FromBus': {df2.loc[latest_match_idx, 'FromBus']}, 'ToBus': {df2.loc[latest_match_idx, 'ToBus']}, ReportingYearNbr: {latest_year}\n"
                )

                f.write(f"Match {count}:\n")
                f.write(
                    f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                )
                f.write(
                    f"dfTads row {latest_match_idx} 'FromBus': {df2.loc[latest_match_idx, 'FromBus']}, 'ToBus': {df2.loc[latest_match_idx, 'ToBus']}, ReportingYearNbr: {latest_year}\n\n"
                )

    return matches

In [76]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["To Bus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"Match {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n\n"
                        )

    return matches

In [77]:
# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:



KeyError: 'To Bus'

In [78]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"Match {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n\n"
                        )

    return matches

In [79]:
# Set the maximum number of matches to display
max_matches = 500

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291662 'FromBus': Waterman, 'ToBus': Sandwich

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291663 'FromBus': Waterman,

In [80]:
# Set the maximum number of matches to display
max_matches = 5000

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291662 'FromBus': Waterman, 'ToBus': Sandwich

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291663 'FromBus': Waterman,

In [81]:
import os
# import sys
# import IPython
import pandas as pd

In [82]:
try:
	fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
	wd = os.path.dirname(fileAddr)
	print("We seem to be working in a JuPyteR Notebook")
except ImportError:
	wd = os.getcwd()
	print("We seem to be working in a regular .py file")


# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [83]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [84]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-84-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [85]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [86]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ]
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [87]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [88]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [89]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [90]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)


# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [91]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches

In [92]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"Match {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n\n"
                        )

    return matches

In [93]:
# Set the maximum number of matches to display
max_matches = 5000

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291662 'FromBus': Waterman, 'ToBus': Sandwich

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291663 'FromBus': Waterman,

In [94]:
import os
# import sys
# import IPython
import pandas as pd

In [95]:
try:
	fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
	wd = os.path.dirname(fileAddr)
	print("We seem to be working in a JuPyteR Notebook")
except ImportError:
	wd = os.getcwd()
	print("We seem to be working in a regular .py file")


# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [96]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [97]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-97-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [98]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [99]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ]
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [100]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [101]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [102]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [103]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)


# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [104]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches

In [105]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"Match {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n\n"
                        )

    return matches

In [106]:
# Set the maximum number of matches to display
max_matches = 5000

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:

Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich

Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich

Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich

Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich

Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich

Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich

Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291662 'FromBus': Waterman, 'ToBus': Sandwich

Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291663 'FromBus': Waterman,

In [107]:
dfTads[(dfTads['FromBus'] == "Zion") & (dfTads['ToBus'] == "Arcadian")]

Empty DataFrame
Columns: [InventoryDataDetailID, InventoryDataID, CompanyName, CompanyCode, NERCID, NERCID_AliasID, ReportingYearNbr, RegionCode, SubRegionName, ElementIdentifierName, ElementIdentifierName_AliasID, FromBus, FromBus_AliasID, ToBus, ToBus_AliasID, TertiaryBus, TertiaryBus_AliasID, Miles, Miles_grp, BESExemptedFlag, NumberOfTerminals, NumberOfTerminals_grp, CircuitTypeCode, VoltageClassCodeName, ParentCode, ConductorsPerPhaseCode, OverheadGroundWireCode, InsulatorTypeCode, CableTypeCode, StructureMaterialCode, StructureTypeCode, CircuitsPerStructureCode, TerrainCode, ElevationCode, InServiceDate, RetirementDate, Comment, CreationDT, ExtractionDT, UpdateDT, DeletionDT, NERC_DataPullDT, ID_SK, Rnk, Slicer, AliasID, IsCurrent]
Index: []

[0 rows x 47 columns]

In [108]:
dfTads[(dfTads['FromBus'] == "Arcadian") & (dfTads['ToBus'] == "Zion")]

InventoryDataDetailID  InventoryDataID                    CompanyName  \
11115                 119129             9405  American Transmission Company   
11116                 119129             9405  American Transmission Company   
11117                 119129             9405  American Transmission Company   
11118                 119129             9405  American Transmission Company   
11119                 119129             9405  American Transmission Company   
11120                 119129             9405  American Transmission Company   
11121                 119129             9405  American Transmission Company   
36262                  24633             5165  American Transmission Company   
36263                  43468             6231  American Transmission Company   
36264                  72631             7296  American Transmission Company   

          CompanyCode    NERCID                      NERCID_AliasID  \
11115  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11116  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11117  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11118  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11119  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11120  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
11121  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
36262  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
36263  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   
36264  NCR00685 | MRO  NCR00685  0xC70034A38B0C36680A0A29FB10DC6C8B   

       ReportingYearNbr RegionCode SubRegionName ElementIdentifierName  ...  \
11115              2016        MRO           MRO                  2222  ...   
11116              2017        MRO           MRO                  2222  ...   
11117              2018        MRO           MRO                  2222  ...   
11118              2019        MRO           MRO                  2222  ...   
11119              2020        MRO           MRO                  2222  ...   
11120              2021        MRO           MRO                  2222  ...   
11121              2022        MRO           MRO                  2222  ...   
36262              2013        MRO           MRO                  2222  ...   
36263              2014        MRO           MRO                  2222  ...   
36264              2015        MRO           MRO                  2222  ...   

      CreationDT ExtractionDT UpdateDT DeletionDT NERC_DataPullDT   ID_SK Rnk  \
11115    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600320   1   
11116    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600321   1   
11117    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600322   1   
11118    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600323   1   
11119    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600324   1   
11120    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600325   1   
11121    41:54.5      30:03.6  29:32.8        NaN         00:13.6  600326   1   
36262    39:07.7      55:11.3  00:39.1        NaN         00:20.1  110613   1   
36263    19:19.5      55:11.3  19:19.5        NaN         00:20.1  118775   1   
36264    24:01.6      55:11.3  24:21.0        NaN         00:20.1  132051   1   

                     Slicer                             AliasID  IsCurrent  
11115  9405 | 119129 | 2016  0x8F0EF705B45DD1C3937953D9361B5234          1  
11116  9405 | 119129 | 2017  0x8F0EF705B45DD1C3937953D9361B5234          1  
11117  9405 | 119129 | 2018  0x8F0EF705B45DD1C3937953D9361B5234          1  
11118  9405 | 119129 | 2019  0x8F0EF705B45DD1C3937953D9361B5234          1  
11119  9405 | 119129 | 2020  0x8F0EF705B45DD1C3937953D9361B5234          1  
11120  9405 | 119129 | 2021  0x8F0EF705B45DD1C3937953D9361B5234          1  
11121  9405 | 119129 | 2022  0x8F0EF705B45D

In [109]:
dfTads[(dfTads['FromBus'] == "Arcadian") & (dfTads['ToBus'] == "Zion")]['ReportingYearNbr']

11115    2016
11116    2017
11117    2018
11118    2019
11119    2020
11120    2021
11121    2022
36262    2013
36263    2014
36264    2015
Name: ReportingYearNbr, dtype: int64

In [110]:
dfTads[(dfTads['FromBus'] == "Arcadian") & (dfTads['ToBus'] == "Zion")]['RetirementData']

KeyError: 'RetirementData'

In [111]:
dfTads[(dfTads['FromBus'] == "Arcadian") & (dfTads['ToBus'] == "Zion")]['RetirementDate']

11115    12/30/22 0:00
11116    12/30/22 0:00
11117    12/30/22 0:00
11118    12/30/22 0:00
11119    12/30/22 0:00
11120    12/30/22 0:00
11121    12/30/22 0:00
36262              NaN
36263              NaN
36264              NaN
Name: RetirementDate, dtype: object

In [112]:
import pandas as pd

def find_matching_rows(df, col1_name, col2_name, value1, value2):
    """
    Finds rows in a DataFrame where a tuple of values matches two columns.

    Args:
        df (pandas.DataFrame): The DataFrame to search.
        col1_name (str): The name of the first column.
        col2_name (str): The name of the second column.
        value1 (str): The first value to match.
        value2 (str): The second value to match.

    Returns:
        pandas.DataFrame: A new DataFrame containing matching rows.
    """

    return df[
        (df[col1_name] == value1) & (df[col2_name] == value2)
        | (df[col1_name] == value2) & (df[col2_name] == value1)
    ]


# Example usage
df = pd.DataFrame(
    {
        "FromBus": ["Arcadian", "Stardust", "Zion", "Zephyr"],
        "ToBus": ["Zion", "Arcadian", "Zephyr", "Arcadian"],
    }
)
matched_df = find_matching_rows(df, "FromBus", "ToBus", "Arcadian", "Zion")
print(matched_df)

    FromBus ToBus
0  Arcadian  Zion


In [113]:
import pandas as pd

def find_tline_by_buses(df, col1_name, col2_name, value1, value2):
    """
    Finds rows in a DataFrame where a tuple of values matches two columns.

    Args:
        df (pandas.DataFrame): The DataFrame to search.
        col1_name (str): The name of the first column.
        col2_name (str): The name of the second column.
        value1 (str): The first value to match.
        value2 (str): The second value to match.

    Returns:
        pandas.DataFrame: A new DataFrame containing matching rows.
    """

    return df[
        (df[col1_name] == value1) & (df[col2_name] == value2)
        | (df[col1_name] == value2) & (df[col2_name] == value1)
    ]


# # Example usage
# df = pd.DataFrame(
#     {
#         "FromBus": ["Arcadian", "Stardust", "Zion", "Zephyr"],
#         "ToBus": ["Zion", "Arcadian", "Zephyr", "Arcadian"],
#     }
# )
# matched_df = find_matching_rows(df, "FromBus", "ToBus", "Arcadian", "Zion")
# print(matched_df)

In [114]:
import os
# import sys
# import IPython
import pandas as pd

from src.helperFunctions import find_tline_by_buses

In [115]:
try:
	fileAddr = __vsc_ipynb_file__ # type: ignore # vscode only, Pylance seems to have an issue with this macro, so ignoring the warning
	wd = os.path.dirname(fileAddr)
	print("We seem to be working in a JuPyteR Notebook")
except ImportError:
	wd = os.getcwd()
	print("We seem to be working in a regular .py file")


# pylint: disable=f-string-without-interpolation line-too-long pointless-statement invalid-name

rawDataFolder = os.path.join(wd, "rawData")
processedDataFolder = os.path.join(wd, "processedData/")

We seem to be working in a JuPyteR Notebook


In [116]:
matchFileAddr = os.path.join(rawDataFolder, "Match_file.csv")
dfMatch = pd.read_csv(matchFileAddr)
colNamesMatch = dfMatch.columns.tolist()
colNamesMatch
matchedIndices = dfMatch['Rec_ID'].notna()
num = sum(matchedIndices)
dfMatched = dfMatch[matchedIndices]
dfMatched.to_excel("dfMatched.xlsx")
sizeMatched0 = dfMatched.shape
print(f"Size of Match_file csv before any filtering: {sizeMatched0[0]}, {sizeMatched0[1]}")

Size of Match_file csv before any filtering: 3080, 53


In [117]:
tadsFileAddr = os.path.join(rawDataFolder, "TADS 2024 AC Inventory.csv")
dfTads0 = pd.read_csv(tadsFileAddr)
sizeTads0 = dfTads0.shape
print(f"Size of TADS db before filtering: {sizeTads0[0]}, {sizeTads0[1]}")
companyNamesTads0 = set(dfTads0.CompanyName)
numCompaniesTads0 = len(companyNamesTads0)
print(f"There are {numCompaniesTads0} unique companies owning tlines in the entire TADS database.")
# display(dftads)

<ipython-input-117-081c3e414d19>:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  dfTads0 = pd.read_csv(tadsFileAddr)


Size of TADS db before filtering: 301152, 47
There are 304 unique companies owning tlines in the entire TADS database.


In [118]:
location = "chicago-ohare"
veloFileAddr = os.path.join(rawDataFolder, "tlines-near-chicago-ohare-raw.xlsx") # tlines which are <= 50miles from `Chicago/Ohare` weather station
print(veloFileAddr)
dfVelo0 = pd.read_excel(veloFileAddr, engine='openpyxl')
sizeVelo0 = dfVelo0.shape
print(f"Size of velocity suite db before any filtering: {sizeVelo0[0]}, {sizeVelo0[1]}")
# dfVelo0

c:\Users\jhaa\Documents\documents_general\extreme-weather-repo\rawData\tlines-near-chicago-ohare-raw.xlsx
Size of velocity suite db before any filtering: 524, 21


In [119]:
# Filter rows with 'Undetermined Company`
# dfVelo = dfVelo0[ dfVelo0['Company Name'] != 'Undetermined Company' ]
# Filter tlines with less than 100kV voltage
dfVelo = dfVelo0.copy()
dfVelo = dfVelo[ dfVelo['Voltage kV'] >= 100 ]
# Filter tlines not currently in service
dfVelo = dfVelo[ dfVelo['Proposed'] == 'In Service']
sizeVelo = dfVelo.shape
print(f"Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': {sizeVelo[0]}, {sizeVelo[1]}")
companyNamesVelo = set(dfVelo['Company Name'])
numCompaniesVelo = len(companyNamesVelo)
print(f"There are {numCompaniesVelo} named companies owning the tlines near {location}")
print(f"Their names are:")
print(companyNamesVelo)
# dfVelo

Size of velocity suite db after filtering for Company Names, Voltage [kV] and 'Proposed': 459, 21
There are 6 named companies owning the tlines near chicago-ohare
Their names are:
{'Undetermined Company', 'AmerenIP', 'Northern Municipal Power Agency', 'American Transmission Co LLC', 'Commonwealth Edison Co', 'Northern Indiana Public Service Co LLC'}


In [120]:
print(f"Now let's see how many tlines are owned by these {numCompaniesVelo} "       "companies in the entire TADS database:")

print(""f"But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.")

companyNamesVelo2Tads = companyNamesVelo.copy()  # Create a copy to avoid modifying the original

# Replace the element using the 'discard' method (more efficient for sets)
companyNamesVelo2Tads.discard("Commonwealth Edison Co")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
companyNamesVelo2Tads.discard("AmerenIP")
companyNamesVelo2Tads.add("Ameren Services Company")
companyNamesVelo2Tads.discard("American Transmission Co LLC")
companyNamesVelo2Tads.add("American Transmission Company")
companyNamesVelo2Tads.discard("Northern Indiana Public Service Co LLC")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Northern Municipal Power Agency")
companyNamesVelo2Tads.add("Northern Indiana Public Service Company [BA")
companyNamesVelo2Tads.discard("Undetermined Company")
companyNamesVelo2Tads.add("Commonwealth Edison Company")
print(companyNamesVelo2Tads)

Now let's see how many tlines are owned by these 6 companies in the entire TADS database:
But first I'll need to rename some companies in vs db to match with the exact strings of the TADS db.
{'Northern Indiana Public Service Company [BA', 'American Transmission Company', 'Ameren Services Company', 'Commonwealth Edison Company'}


In [121]:
dfTads = dfTads0.copy()
dfTads = dfTads[dfTads['CompanyName'].isin(companyNamesVelo2Tads)]
voltageClassesTads0 = set(dfTads['VoltageClassCodeName'])
print(voltageClassesTads0)
voltageClassesAllowedTads = voltageClassesTads0.copy()
voltageClassesAllowedTads.discard("0-99 kV")

dfTads = dfTads[dfTads['VoltageClassCodeName'].isin(voltageClassesAllowedTads)]

sizeTads = dfTads.shape
print(f"Size of TADS db after filtering: {sizeTads[0]}, {sizeTads[1]}")

{'200-299 kV', '600-799 kV', '300-399 kV', '100-199 kV'}
Size of TADS db after filtering: 16052, 47


In [122]:
dfVeloMatched = dfVelo[dfVelo['Rec_ID'].isin(dfMatched['Rec_ID'])]
# dfVeloMatched
veloMatchedAddr = os.path.join(processedDataFolder, "dfVeloMatched.xlsx")
dfVeloMatched.to_excel("dfVeloMatched.xlsx")
# sizeVelo = dfVelo.shape
# print(f"Size of velocity suite db before any filtering: {sizeVelo[0]}, {sizeVelo[1]}")
# dfVeloMatched

In [123]:
# def find_partial_matches(df1, col1, df2, col2):
#     return df1[df1[col1].str.contains('|'.join(df2[col2].dropna()), na=False)]

# # Finding partial matches
# matchV1T1 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'FromBus')
# matchV1T2 = find_partial_matches(dfVelo, 'From Sub', dfTads, 'ToBus')
# matchV2T1 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'FromBus')
# matchV2T2 = find_partial_matches(dfVelo, 'To Sub', dfTads, 'ToBus')

# # Display results
# print("Matching rows from 'From Sub' to 'FromBus':")
# print(matchV1T1)

# print("\nMatching rows from 'From Sub' to 'ToBus':")
# print(matchV1T2)

# print("\nMatching rows from 'To Sub' to 'FromBus':")
# print(matchV2T1)

# print("\nMatching rows from 'To Sub' to 'ToBus':")
# print(matchV2T2)


# # %%
# # Assuming matchV1T1, matchV2T1, matchV1T2, and matchV2T2 are DataFrames with an index

# intersection_V1T1_V2T2 = matchV1T1[matchV1T1.index.isin(matchV2T2.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T1 and matchV2T2:")
# print(intersection_V1T1_V2T2)

# # %%
# intersection_V1T2_V2T1 = matchV1T2[matchV1T2.index.isin(matchV2T1.index)]

# # Print the intersection DataFrame
# print("Intersection of matchV1T2 and matchV2T1:")
# print(intersection_V1T2_V2T1)

In [124]:
# Function to find and display matches with verbosity
# def find_and_display_matches(df1, df2, max_matches=5):
#     matches = []
#     count = 0

#     for idx1, row1 in df1.iterrows():
#         match_found = False
#         for idx2, row2 in df2.iterrows():
#             if (row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']) or \
#                (row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']):
#                 matches.append((idx1, idx2))
#                 count += 1
#                 if row1['From Sub'] == row2['FromBus'] and row1['To Sub'] == row2['ToBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n")
#                 elif row1['From Sub'] == row2['ToBus'] and row1['To Sub'] == row2['FromBus']:
#                     print(f"Match {count}:")
#                     print(f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}")
#                     print(f"dfTads row {idx2} 'FromBus': {row2['ToBus']}, 'ToBus': {row2['FromBus']}\n")
#                 match_found = True
#                 if count >= max_matches:
#                     return matches
#                 break
#         if match_found:
#             continue
#     return matches

In [125]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"Match {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n\n"
                        )

    return matches

In [127]:
# VS: "Voltage Class kV" is among "100-161", "345", "735 and Above",

In [128]:
def find_and_display_matches(
    df1, df2, max_matches=5, output_file="matches.txt", output_dir="./processedData"
):
    matches = []

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)  # Create directory if needed

    with open(os.path.join(output_dir, output_file), "w") as f:
        for idx1, row1 in df1.iterrows():
            match_found = False

            for idx2, row2 in df2.iterrows():
                if (
                    row1["From Sub"] == row2["FromBus"]
                    and row1["To Sub"] == row2["ToBus"]
                ) or (
                    row1["From Sub"] == row2["ToBus"]
                    and row1["To Sub"] == row2["FromBus"]
                ):
                    matches.append((idx1, idx2))
                    match_found = True  # Set match found once a match is identified

                    # Print/write details for all matches (up to max_matches)
                    if match_found and len(matches) <= max_matches:
                        print(f"\nMatch {len(matches)}:")
                        print(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}"
                        )
                        print(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        f.write(f"Match {len(matches)}:\n")
                        f.write(
                            f"dfVelo row {idx1} 'From Sub': {row1['From Sub']}, 'To Sub': {row1['To Sub']}\n"
                        )
                        f.write(
                            f"dfTads row {idx2} 'FromBus': {row2['FromBus']}, 'ToBus': {row2['ToBus']}\n"
                        )

                        # Check for retirement date and print/write
                    if not pd.isna(row2["RetirementDate"]):
                        retirement_date = row2["RetirementDate"]
                        print(f"dfTads row {idx2}: Retired on {retirement_date}")
                        f.write(f"dfTads row {idx2}: Retired on {retirement_date}\n")

    return matches

In [129]:
# Set the maximum number of matches to display
max_matches = 5000

# Finding exact matches with verbose output
print("Finding exact matches with verbose output:\n")
exact_matches = find_and_display_matches(dfVelo,  dfTads, max_matches)

Finding exact matches with verbose output:


Match 1:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291656 'FromBus': Waterman, 'ToBus': Sandwich


Match 2:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291657 'FromBus': Waterman, 'ToBus': Sandwich


Match 3:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291658 'FromBus': Waterman, 'ToBus': Sandwich


Match 4:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291659 'FromBus': Waterman, 'ToBus': Sandwich


Match 5:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291660 'FromBus': Waterman, 'ToBus': Sandwich


Match 6:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291661 'FromBus': Waterman, 'ToBus': Sandwich


Match 7:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291662 'FromBus': Waterman, 'ToBus': Sandwich


Match 8:
dfVelo row 10 'From Sub': Sandwich, 'To Sub': Waterman
dfTads row 291663 'FromBus': W

In [130]:
find_tline_by_buses(dfTads, 'FromBus', 'ToBus', 'Sandwich', 'Waterman')

InventoryDataDetailID  InventoryDataID                  CompanyName  \
291656                  73957             6850  Commonwealth Edison Company   
291657                 118974             9400  Commonwealth Edison Company   
291658                 118974             9400  Commonwealth Edison Company   
291659                 118974             9400  Commonwealth Edison Company   
291660                 118974             9400  Commonwealth Edison Company   
291661                 118974             9400  Commonwealth Edison Company   
291662                 118974             9400  Commonwealth Edison Company   
291663                 118974             9400  Commonwealth Edison Company   
291664                 118974             9400  Commonwealth Edison Company   
291665                 118974             9400  Commonwealth Edison Company   

                       CompanyCode    NERCID  \
291656  NCR08013 | RFC | RFC - PJM  NCR08013   
291657  NCR08013 | RFC | RFC - PJM  NCR08013   
291658  NCR08013 | RFC | RFC - PJM  NCR08013   
291659  NCR08013 | RFC | RFC - PJM  NCR08013   
291660  NCR08013 | RFC | RFC - PJM  NCR08013   
291661  NCR08013 | RFC | RFC - PJM  NCR08013   
291662  NCR08013 | RFC | RFC - PJM  NCR08013   
291663  NCR08013 | RFC | RFC - PJM  NCR08013   
291664  NCR08013 | RFC | RFC - PJM  NCR08013   
291665  NCR08013 | RFC | RFC - PJM  NCR08013   

                            NERCID_AliasID  ReportingYearNbr RegionCode  \
291656  0xCC2BCCB6A749329A905A8A66AA5A99DB              2015        RFC   
291657  0xCC2BCCB6A749329A905A8A66AA5A99DB              2016        RFC   
291658  0xCC2BCCB6A749329A905A8A66AA5A99DB              2017        RFC   
291659  0xCC2BCCB6A749329A905A8A66AA5A99DB              2018        RFC   
291660  0xCC2BCCB6A749329A905A8A66AA5A99DB              2019        RFC   
291661  0xCC2BCCB6A749329A905A8A66AA5A99DB              2020        RFC   
291662  0xCC2BCCB6A749329A905A8A66AA5A99DB              2021        RFC   
291663  0xCC2BCCB6A749329A905A8A66AA5A99DB              2022        RFC   
291664  0xCC2BCCB6A749329A905A8A66AA5A99DB              2023        RFC   
291665  0xCC2BCCB6A749329A905A8A66AA5A99DB              2024        RFC   

       SubRegionName ElementIdentifierName  ... CreationDT ExtractionDT  \
291656     RFC - PJM                 11301  ...    22:46.9      10:05.5   
291657     RFC - PJM                 11301  ...    33:22.9      10:05.5   
291658     RFC - PJM                 11301  ...    33:22.9      10:05.5   
291659     RFC - PJM                 11301  ...    33:22.9      30:10.9   
291660     RFC - PJM                 11301  ...    33:22.9      10:03.3   
291661     RFC - PJM                 11301  ...    33:22.9      10:09.3   
291662     RFC - PJM                 11301  ...    33:22.9      05:15.6   
291663     RFC - PJM                 11301  ...    33:22.9      05:09.6   
291664     RFC - PJM                 11301  ...    33:22.9      05:09.2   
291665     RFC - PJM                 11301  ...    33:22.9      05:07.9   

       UpdateDT DeletionDT NERC_DataPullDT   ID_SK Rnk                Slicer  \
291656  08:34.2        NaN         00:00.9  217148   1   6850 | 73957 | 2015   
291657  08:34.2        NaN         00:00.9  217621   1  9400 | 118974 | 2016   
291658  08:34.2        NaN         00:00.9  217622   1  9400 | 118974 | 2017   
291659  28:34.6        NaN         00:01.5  249849   1  9400 | 118974 | 2018   
291660  06:27.5        NaN         00:02.5  309008   1  9400 | 118974 | 2019   
291661  07:32.0        NaN         04:08.8  362960   1  9400 | 118974 | 2020   
291662  00:02.1        NaN         03:26.9  394540   1  9400 | 118974 | 2021   
291663  02:23.2        NaN         01:11.3  502759   1  9400 | 118974 | 2022   
291664  00:01.0        NaN         01:16.2  546123   1  9400 | 118974 | 2023   
291665  00:01.0        NaN         01:21.7  651052   1  9400 | 118974 | 2024   

                                   AliasID  IsCurrent  
291656  0x73234AE5CA

In [131]:
find_tline_by_buses(dfTads, 'FromBus', 'ToBus', 'Waterman', 'Sandwich')

InventoryDataDetailID  InventoryDataID                  CompanyName  \
291656                  73957             6850  Commonwealth Edison Company   
291657                 118974             9400  Commonwealth Edison Company   
291658                 118974             9400  Commonwealth Edison Company   
291659                 118974             9400  Commonwealth Edison Company   
291660                 118974             9400  Commonwealth Edison Company   
291661                 118974             9400  Commonwealth Edison Company   
291662                 118974             9400  Commonwealth Edison Company   
291663                 118974             9400  Commonwealth Edison Company   
291664                 118974             9400  Commonwealth Edison Company   
291665                 118974             9400  Commonwealth Edison Company   

                       CompanyCode    NERCID  \
291656  NCR08013 | RFC | RFC - PJM  NCR08013   
291657  NCR08013 | RFC | RFC - PJM  NCR08013   
291658  NCR08013 | RFC | RFC - PJM  NCR08013   
291659  NCR08013 | RFC | RFC - PJM  NCR08013   
291660  NCR08013 | RFC | RFC - PJM  NCR08013   
291661  NCR08013 | RFC | RFC - PJM  NCR08013   
291662  NCR08013 | RFC | RFC - PJM  NCR08013   
291663  NCR08013 | RFC | RFC - PJM  NCR08013   
291664  NCR08013 | RFC | RFC - PJM  NCR08013   
291665  NCR08013 | RFC | RFC - PJM  NCR08013   

                            NERCID_AliasID  ReportingYearNbr RegionCode  \
291656  0xCC2BCCB6A749329A905A8A66AA5A99DB              2015        RFC   
291657  0xCC2BCCB6A749329A905A8A66AA5A99DB              2016        RFC   
291658  0xCC2BCCB6A749329A905A8A66AA5A99DB              2017        RFC   
291659  0xCC2BCCB6A749329A905A8A66AA5A99DB              2018        RFC   
291660  0xCC2BCCB6A749329A905A8A66AA5A99DB              2019        RFC   
291661  0xCC2BCCB6A749329A905A8A66AA5A99DB              2020        RFC   
291662  0xCC2BCCB6A749329A905A8A66AA5A99DB              2021        RFC   
291663  0xCC2BCCB6A749329A905A8A66AA5A99DB              2022        RFC   
291664  0xCC2BCCB6A749329A905A8A66AA5A99DB              2023        RFC   
291665  0xCC2BCCB6A749329A905A8A66AA5A99DB              2024        RFC   

       SubRegionName ElementIdentifierName  ... CreationDT ExtractionDT  \
291656     RFC - PJM                 11301  ...    22:46.9      10:05.5   
291657     RFC - PJM                 11301  ...    33:22.9      10:05.5   
291658     RFC - PJM                 11301  ...    33:22.9      10:05.5   
291659     RFC - PJM                 11301  ...    33:22.9      30:10.9   
291660     RFC - PJM                 11301  ...    33:22.9      10:03.3   
291661     RFC - PJM                 11301  ...    33:22.9      10:09.3   
291662     RFC - PJM                 11301  ...    33:22.9      05:15.6   
291663     RFC - PJM                 11301  ...    33:22.9      05:09.6   
291664     RFC - PJM                 11301  ...    33:22.9      05:09.2   
291665     RFC - PJM                 11301  ...    33:22.9      05:07.9   

       UpdateDT DeletionDT NERC_DataPullDT   ID_SK Rnk                Slicer  \
291656  08:34.2        NaN         00:00.9  217148   1   6850 | 73957 | 2015   
291657  08:34.2        NaN         00:00.9  217621   1  9400 | 118974 | 2016   
291658  08:34.2        NaN         00:00.9  217622   1  9400 | 118974 | 2017   
291659  28:34.6        NaN         00:01.5  249849   1  9400 | 118974 | 2018   
291660  06:27.5        NaN         00:02.5  309008   1  9400 | 118974 | 2019   
291661  07:32.0        NaN         04:08.8  362960   1  9400 | 118974 | 2020   
291662  00:02.1        NaN         03:26.9  394540   1  9400 | 118974 | 2021   
291663  02:23.2        NaN         01:11.3  502759   1  9400 | 118974 | 2022   
291664  00:01.0        NaN         01:16.2  546123   1  9400 | 118974 | 2023   
291665  00:01.0        NaN         01:21.7  651052   1  9400 | 118974 | 2024   

                                   AliasID  IsCurrent  
291656  0x73234AE5CA

In [132]:
def find_tline_by_buses(
    df,
    value1,
    value2, 
    col1_name='FromBus',
    col2_name='ToBus',
):
    """
    Finds rows in a DataFrame where a tuple of values matches two columns.

    Args:
        df (pandas.DataFrame): The DataFrame to search.
        col1_name (str): The name of the first column.
        col2_name (str): The name of the second column.
        value1 (str): The first value to match.
        value2 (str): The second value to match.

    Returns:
        pandas.DataFrame: A new DataFrame containing matching rows.
    """

    return df[
        (df[col1_name] == value1) & (df[col2_name] == value2)
        | (df[col1_name] == value2) & (df[col2_name] == value1)
    ]


# # Example usage
# df = pd.DataFrame(
#     {
#         "FromBus": ["Arcadian", "Stardust", "Zion", "Zephyr"],
#         "ToBus": ["Zion", "Arcadian", "Zephyr", "Arcadian"],
#     }
# )
# matched_df = find_matching_rows(df, "FromBus", "ToBus", "Arcadian", "Zion")
# print(matched_df)

In [133]:
def find_tline_by_buses(
    df,
    value1,
    value2, 
    col1_name='FromBus',
    col2_name='ToBus',
):
    """
    Finds rows in a DataFrame where a tuple of values matches two columns.

    Args:
        df (pandas.DataFrame): The DataFrame to search.
        col1_name (str): The name of the first column.
        col2_name (str): The name of the second column.
        value1 (str): The first value to match.
        value2 (str): The second value to match.

    Returns:
        pandas.DataFrame: A new DataFrame containing matching rows.
    """

    return df[
        (df[col1_name] == value1) & (df[col2_name] == value2)
        | (df[col1_name] == value2) & (df[col2_name] == value1)
    ]


# Example usage
df = pd.DataFrame(
    {
        "FromBus": ["Arcadian", "Stardust", "Zion", "Zephyr"],
        "ToBus": ["Zion", "Arcadian", "Zephyr", "Arcadian"],
    }
)
matched_df = find_tline_by_buses(df, "Arcadian", "Zion")
print(matched_df)

    FromBus ToBus
0  Arcadian  Zion


In [134]:
def find_tline_by_buses(
    df,
    value1,
    value2, 
    col1_name='FromBus',
    col2_name='ToBus',
):
    """
    Finds rows in a DataFrame where a tuple of values matches two columns.

    Args:
        df (pandas.DataFrame): The DataFrame to search.
        col1_name (str): The name of the first column.
        col2_name (str): The name of the second column.
        value1 (str): The first value to match.
        value2 (str): The second value to match.

    Returns:
        pandas.DataFrame: A new DataFrame containing matching rows.
    """

    return df[
        (df[col1_name] == value1) & (df[col2_name] == value2)
        | (df[col1_name] == value2) & (df[col2_name] == value1)
    ]


# Example usage
df = pd.DataFrame(
    {
        "FromBus": ["Arcadian", "Stardust", "Zion", "Zephyr"],
        "ToBus": ["Zion", "Arcadian", "Zephyr", "Arcadian"],
    }
)
matched_df = find_tline_by_buses(df, "Arcadian", "Zion")
print(matched_df)

    FromBus ToBus
0  Arcadian  Zion


In [ ]:
find_tline_by_buses(dfTads, "Arcadian", "Zion")

In [ ]:
find_tline_by_buses(dfTads, "")